In [ ]:
# !pip install spotipy

Imports

In [1]:
import AccountInfo

In [2]:
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials

sp = spotipy.Spotify(auth_manager=SpotifyClientCredentials(client_id= AccountInfo.client_id,
                                                           client_secret= AccountInfo.client_secret))

In [3]:
import pandas as pd
from bs4 import BeautifulSoup as bs
import numpy as np

Load data and clean

In [4]:
topsongs = pd.read_csv('Data/spotifyTopSongs.tsv')

In [5]:
topsongs.drop("Unnamed: 0", axis = 1, inplace=True)

In [6]:
topsongs

Pos             Artist                                          Title  \
0        1         The Weeknd                                Blinding Lights   
1        2         Ed Sheeran                                   Shape of You   
2        3      Lewis Capaldi                              Someone You Loved   
3        4        Tones And I                                   Dance Monkey   
4        5        Post Malone  Sunflower - Spider-Man: Into the Spider-Verse   
...    ...                ...                                            ...   
6175  6176       Mariah Carey                                       Infinity   
6176  6177  Twenty One Pilots                                   Fairly Local   
6177  6178           Ludacris                                     Good Lovin   
6178  6179               iSHi                                        Push It   
6179  6180     Handsome Ghost                                          Steps   

      Wks   T10   Pk   (x?)  PkStreams       Total  
0     172  64.0    1  (x13)   52375259  3406980588  
1     308  34.0    1  (x14)   64217796  3302350300  
2     218  15.0    4    NaN   24962682  2623186016  
3     151  41.0    1  (x17)   52055226  2538070349  
4     225  31.0    1   (x2)   34579416  2498983472  
...   ...   ...  ...    ...        ...         ...  
6175    1   NaN  220    NaN     177495      177495  
6176    1   NaN  234    NaN     176713      176713  
6177    1   NaN  223    NaN     174256      174256  
6178    1   NaN  236    NaN     173886      173886  
6179    1   NaN  239    NaN     166910      166910  

[6180 rows x 9 columns]

spotify does NOT let you pull streaming numbers with its API. To obtain streaming data, one can webscrape it. In the interest of time, I will not be scraping this data. However, you can use POPULARITY: which takes into account total number of streams and the recency of those streams. Because we are discover how to make a hit NOW (and not 5 years ago), This metric may be more beneficial than total number of streams\n

The API also does not associate a song with a particular genre. That information is gotten from the artists information.

In [7]:
# New column 'info' that is the information from that song returned from the spotify API
topsongs['info'] = topsongs.apply(lambda x: sp.search(q=f"track: \"{x['Title']}\" artist: \"{x['Artist']}\"", limit = 1), axis = 1)

KeyboardInterrupt: 

In [ ]:
#Export to CSV so we dont have to do multiple times
topsongs.to_csv('Data/spotifyTopSongsWithAPI.tsv')

In [ ]:
#new column items that grabs the items portion of the info structure
topsongs['items'] = topsongs.apply(lambda x: x['info']['tracks']['items'], axis = 1)

In [ ]:
# to see if there are any times spotify did not return a result
topsongs[topsongs["items"].str.len() == 0]

The only song in this list that the query could not find is Groupie by Samir & Viktor. Upon further investigation, this song is undiscoverable because it is unvailable in my current region

In [112]:
#artists column that lists artist names and ID
topsongs['artists'] = topsongs.apply(lambda x: [{i['id']:i['name']}for i in x['items'][0]['artists']] if len(x['items']) != 0 else np.nan, axis = 1)

In [123]:
#add songids to the table
topsongs['songid'] = topsongs.apply(lambda x: x['items'][0]['id'] if len(x['items']) != 0 else np.nan, axis = 1)

In [185]:
#add popularity to the table
topsongs['popularity'] = topsongs.apply(lambda x: x['items'][0]['popularity'] if len(x['items']) != 0 else np.nan, axis = 1)

In [186]:
topsongs#['songid']

Pos             Artist                                          Title  \
0        1         The Weeknd                                Blinding Lights   
1        2         Ed Sheeran                                   Shape of You   
2        3      Lewis Capaldi                              Someone You Loved   
3        4        Tones And I                                   Dance Monkey   
4        5        Post Malone  Sunflower - Spider-Man: Into the Spider-Verse   
...    ...                ...                                            ...   
6175  6176       Mariah Carey                                       Infinity   
6176  6177  Twenty One Pilots                                   Fairly Local   
6177  6178           Ludacris                                     Good Lovin   
6178  6179               iSHi                                        Push It   
6179  6180     Handsome Ghost                                          Steps   

      Wks   T10   Pk   (x?)  PkStreams       Total  \
0     172  64.0    1  (x13)   52375259  3406980588   
1     308  34.0    1  (x14)   64217796  3302350300   
2     218  15.0    4    NaN   24962682  2623186016   
3     151  41.0    1  (x17)   52055226  2538070349   
4     225  31.0    1   (x2)   34579416  2498983472   
...   ...   ...  ...    ...        ...         ...   
6175    1   NaN  220    NaN     177495      177495   
6176    1   NaN  234    NaN     176713      176713   
6177    1   NaN  223    NaN     174256      174256   
6178    1   NaN  236    NaN     173886      173886   
6179    1   NaN  239    NaN     166910      166910   

                                                   info  \
0     {'tracks': {'href': 'https://api.spotify.com/v...   
1     {'tracks': {'href': 'https://api.spotify.com/v...   
2     {'tracks': {'href': 'https://api.spotify.com/v...   
3     {'tracks': {'href': 'https://api.spotify.com/v...   
4     {'tracks': {'href': 'https://api.spotify.com/v...   
...                                                 ...   
6175  {'tracks': {'href': 'https://api.spotify.com/v...   
6176  {'tracks': {'href': 'https://api.spotify.com/v...   
6177  {'tracks': {'href': 'https://api.spotify.com/v...   
6178  {'tracks': {'href': 'https://api.spotify.com/v...   
6179  {'tracks': {'href': 'https://api.spotify.com/v...   

                                                  items  \
0     [{'album': {'album_group': 'album', 'album_typ...   
1     [{'album': {'album_group': 'album', 'album_typ...   
2     [{'album': {'album_group': 'album', 'album_typ...   
3     [{'album': {'album_group': 'single', 'album_ty...   
4     [{'album': {'album_group': 'compilation', 'alb...   
...                                                 ...   
6175  [{'album': {'album_group': 'compilation', 'alb...   
6176  [{'album': {'album_group': 'album', 'album_typ...   
6177  [{'album': {'album_group': 'album', 'album_typ...   
6178  [{'album': {'album_group': 'album', 'album_typ...   
6179  [{'album': {'album_group': 'single', 'album_ty...   

                                                artists  \
0            [{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}]   
1            [{'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}]   
2         [{'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}]   
3           [{'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}]   
4     [{'246dkjvS1zLTtiykXe5h60': 'Post Malone'}, {'...   
...                                                 ...   
6175       [{'4iHNK0tOyZPYnBU7nGAgpQ': 'Mariah Carey'}]   
6176  [{'3YQKmKGau1PzlVlkL1iodx': 'Twenty One Pilots'}]   
6177  [{'3ipn9JLAPI5GUEo4y4jcoi': 'Ludacris'}, {'360...   
6178  [{'6Dy7Ex5zlTLgXbsB92rPji': 'iSHi'}, {'2rRz9oF...   
6179     [{'3IaqL9bsZtYJkqNLiovVho': 'Handsome Ghost'}]   

                      songid  popularity  
0     0VjIjW4GlUZAMYd2vXMi3b        90.0  
1     7qiZfU4dY1lWllzX7mPBI3        85.0  
2     7qEHsqek33rTcFNT9PFqLf        87.0  
3     2XU0oxnq2qxCpomAAuJY8K        76.0  
4     3KkXRkHbMCARz0aVfEt68P        81.0  
...         

In [121]:
topsongs['items'][0][0]['id']

'0VjIjW4GlUZAMYd2vXMi3b'

In [ ]:
for row in topsongs:
    print(row)
    #     results = sp.search(q=f"track: \"{title}\" artist: \"{artist}\"", limit = 1,)

In [ ]:
artist = topsongs[['Artist','Title']].loc[4][0]
title  = topsongs[['Artist','Title']].loc[4][1]
# results = sp.search(q=f"song: \"{title}\" artist: \"{artist}\"", limit = 1,)
results = sp.search(q=f"track: \"{title}\" artist: \"{artist}\"", limit = 1,)
# print(results) 
results
#spotify:track:7qiZfU4dY1lWllzX7mPBI3
# track_uri = results['tracks']['items'][0]['uri']
# results['tracks']['items'][0]['uri']

In [ ]:
results['tracks']['items'][0]['artists']

In [ ]:
for i in results['tracks']['items'][0]['artists']:
    print(f"name: {i['name']}, id: {i['id']}")

In [ ]:
BASE_URL = 'https://api.spotify.com/v1/'

In [ ]:
print(f'{artist}{title}')

In [ ]:
for idx, track in enumerate(results['tracks']['items']):
    print(idx, track['name'])

In [ ]:
#new row = 
# df['column']= df.apply(lambda x: sp.search(q=f"track: \"{x['Title']}\" artist: \"{x['Artist']}\"", limit = 1,)
# topsongs.assign(test=lambda x:"track: "+{x.Title})['test']
topsongs['test'] = topsongs.apply(lambda x: "track: "+ str({x['Title']}), axis = 1)

In [ ]:
topsongs

In [ ]:
topsongs['test'] = topsongs.apply(lambda x: "track: "+ str({x['Title']}), axis = 1)


spotify does NOT let you pull streaming numbers with its API. To obtain streaming data, one can webscrape it. In the interest of time, I will not be scraping this data. However, you can use POPULARITY: which takes into account total number of streams and the recency of those streams. Because we are discover how to make a hit NOW (and not 5 years ago), This metric may be more beneficial than total number of streams\n

The API also does not associate a song with a particular genre. That information is gotten from the artists information.

In [7]:
topsongs['info'] = topsongs.apply(lambda x: sp.search(q=f"track: \"{x['Title']}\" artist: \"{x['Artist']}\"", limit = 1), axis = 1)

In [8]:
topsongs

Pos             Artist                                          Title  \
0        1         The Weeknd                                Blinding Lights   
1        2         Ed Sheeran                                   Shape of You   
2        3      Lewis Capaldi                              Someone You Loved   
3        4        Tones And I                                   Dance Monkey   
4        5        Post Malone  Sunflower - Spider-Man: Into the Spider-Verse   
...    ...                ...                                            ...   
6175  6176       Mariah Carey                                       Infinity   
6176  6177  Twenty One Pilots                                   Fairly Local   
6177  6178           Ludacris                                     Good Lovin   
6178  6179               iSHi                                        Push It   
6179  6180     Handsome Ghost                                          Steps   

      Wks   T10   Pk   (x?)  PkStreams       Total  \
0     172  64.0    1  (x13)   52375259  3406980588   
1     308  34.0    1  (x14)   64217796  3302350300   
2     218  15.0    4    NaN   24962682  2623186016   
3     151  41.0    1  (x17)   52055226  2538070349   
4     225  31.0    1   (x2)   34579416  2498983472   
...   ...   ...  ...    ...        ...         ...   
6175    1   NaN  220    NaN     177495      177495   
6176    1   NaN  234    NaN     176713      176713   
6177    1   NaN  223    NaN     174256      174256   
6178    1   NaN  236    NaN     173886      173886   
6179    1   NaN  239    NaN     166910      166910   

                                                   info  
0     {'tracks': {'href': 'https://api.spotify.com/v...  
1     {'tracks': {'href': 'https://api.spotify.com/v...  
2     {'tracks': {'href': 'https://api.spotify.com/v...  
3     {'tracks': {'href': 'https://api.spotify.com/v...  
4     {'tracks': {'href': 'https://api.spotify.com/v...  
...                                                 ...  
6175  {'tracks': {'href': 'https://api.spotify.com/v...  
6176  {'tracks': {'href': 'https://api.spotify.com/v...  
6177  {'tracks': {'href': 'https://api.spotify.com/v...  
6178  {'tracks': {'href': 'https://api.spotify.com/v...  
6179  {'tracks': {'href': 'https://api.spotify.com/v...  

[6180 rows x 10 columns]

In [9]:
topsongs.to_csv('Data/spotifyTopSongsWithAPI.tsv')

In [18]:
topsongs['info'][0]['tracks']['items']

[{'album': {'album_group': 'album',
   'album_type': 'album',
   'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'},
     'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ',
     'id': '1Xyo4u8uXC1ZmMpatF05PJ',
     'name': 'The Weeknd',
     'type': 'artist',
     'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}],
   'available_markets': ['AD',
    'AE',
    'AG',
    'AL',
    'AM',
    'AO',
    'AR',
    'AT',
    'AU',
    'AZ',
    'BA',
    'BB',
    'BD',
    'BE',
    'BF',
    'BG',
    'BH',
    'BI',
    'BJ',
    'BN',
    'BO',
    'BR',
    'BS',
    'BT',
    'BW',
    'BY',
    'BZ',
    'CA',
    'CD',
    'CG',
    'CH',
    'CI',
    'CL',
    'CM',
    'CO',
    'CR',
    'CV',
    'CW',
    'CY',
    'CZ',
    'DE',
    'DJ',
    'DK',
    'DM',
    'DO',
    'DZ',
    'EC',
    'EE',
    'EG',
    'ES',
    'FI',
    'FJ',
    'FM',
    'FR',
    'GA',
    'GB',
    'GD',
    'GE',
    'GH',
    'GM

In [20]:
topsongs['items'] = topsongs.apply(lambda x: x['info']['tracks']['items'], axis = 1)

In [25]:
topsongs['items']

[{'album': {'album_group': 'album',
   'album_type': 'album',
   'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/6eUKZXaKkcviH0Ku9w2n3V'},
     'href': 'https://api.spotify.com/v1/artists/6eUKZXaKkcviH0Ku9w2n3V',
     'id': '6eUKZXaKkcviH0Ku9w2n3V',
     'name': 'Ed Sheeran',
     'type': 'artist',
     'uri': 'spotify:artist:6eUKZXaKkcviH0Ku9w2n3V'}],
   'available_markets': ['AD',
    'AE',
    'AG',
    'AL',
    'AM',
    'AO',
    'AR',
    'AT',
    'AU',
    'AZ',
    'BA',
    'BB',
    'BD',
    'BE',
    'BF',
    'BG',
    'BH',
    'BI',
    'BJ',
    'BN',
    'BO',
    'BR',
    'BS',
    'BT',
    'BW',
    'BY',
    'BZ',
    'CA',
    'CD',
    'CG',
    'CH',
    'CI',
    'CL',
    'CM',
    'CO',
    'CR',
    'CV',
    'CW',
    'CY',
    'CZ',
    'DE',
    'DJ',
    'DK',
    'DM',
    'DO',
    'DZ',
    'EC',
    'EE',
    'EG',
    'ES',
    'ET',
    'FI',
    'FJ',
    'FM',
    'FR',
    'GA',
    'GB',
    'GD',
    'GE',
    'GH

In [29]:
topsongs[topsongs["items"].str.len() == 0]

Pos          Artist    Title  Wks  T10   Pk (x?)  PkStreams    Total  \
5283  5284  Samir & Viktor  Groupie    4  NaN  146  NaN    1469139  4955784   

                                                   info items  
5283  {'tracks': {'href': 'https://api.spotify.com/v...    []

The only song in this list that the query could not find is Groupie by Samir & Viktor. Upon further investigation, this song is undiscoverable because it is unvailable in my current region

In [27]:
sp.search(q=f"track: \"asdfasdfa\" artist: \"sadsjlkgdahgadh\"", limit = 1,)['tracks']['items']

[]

In [44]:
topsongs['items'][1][0]['artists'][0]

{'external_urls': {'spotify': 'https://open.spotify.com/artist/6eUKZXaKkcviH0Ku9w2n3V'},
 'href': 'https://api.spotify.com/v1/artists/6eUKZXaKkcviH0Ku9w2n3V',
 'id': '6eUKZXaKkcviH0Ku9w2n3V',
 'name': 'Ed Sheeran',
 'type': 'artist',
 'uri': 'spotify:artist:6eUKZXaKkcviH0Ku9w2n3V'}

In [ ]:
# topsongs['items'][rowindex][0]['artists'][artistindex]['id']
topsongs['items'][1][0]['artists'][0]['id']

In [ ]:
topsongs['artists']= 

In [49]:
for artist in topsongs['items'][0][0]['artists']:
    print(artist['id'])

1Xyo4u8uXC1ZmMpatF05PJ


In [112]:
topsongs['artists'] = topsongs.apply(lambda x: [{i['id']:i['name']}for i in x['items'][0]['artists']] if len(x['items']) != 0 else np.nan, axis = 1)

In [113]:
topsongs['items'][0][0]['artists']

[{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'},
  'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ',
  'id': '1Xyo4u8uXC1ZmMpatF05PJ',
  'name': 'The Weeknd',
  'type': 'artist',
  'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}]

In [114]:
topsongs['artists']

0              [{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}]
1              [{'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}]
2           [{'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}]
3             [{'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}]
4       [{'246dkjvS1zLTtiykXe5h60': 'Post Malone'}, {'...
                              ...                        
6175         [{'4iHNK0tOyZPYnBU7nGAgpQ': 'Mariah Carey'}]
6176    [{'3YQKmKGau1PzlVlkL1iodx': 'Twenty One Pilots'}]
6177    [{'3ipn9JLAPI5GUEo4y4jcoi': 'Ludacris'}, {'360...
6178    [{'6Dy7Ex5zlTLgXbsB92rPji': 'iSHi'}, {'2rRz9oF...
6179       [{'3IaqL9bsZtYJkqNLiovVho': 'Handsome Ghost'}]
Name: artists, Length: 6180, dtype: object

In [191]:
# topsongs['artists']
artists = set()
for song in topsongs['artists']:
    if type(song) != float:
        for artist in song:
            keys =list(artist.keys()) 
            artists.add(keys[0])
artists

{'1aQbanZ6xPrOtTYtsMdm3Q',
 '1U1el3k54VvEUzo3ybLPlM',
 '5j21TGkrNEAJe3gG9VlS34',
 '6xHUXzrfhFgnIv86EBR3Ml',
 '2nm38smINjms1LtczR0Cei',
 '3hPPNy5OBzCU1icQO7Nrok',
 '6VuMaDnrHyPL1p4EHjYLi7',
 '5wTdspmxzb8V4ZjvDodpBo',
 '5NW2uPFatEKjZQ5gpWD8HO',
 '0pePYDrJGk8gqMRbXrLJC8',
 '3ATyg4fGC9F8trfb0GRWmX',
 '3Oim8XBPbznAa8Jj8QzNc8',
 '3aQeKQSyrW4qWr35idm0cy',
 '3uwAm6vQy7kWPS2bciKWx9',
 '7jy3rLJdDQY21OgRLCZ9sD',
 '12vb80Km0Ew53ABfJOepVz',
 '3p3jPcp8b7WL9XYj4xlsWj',
 '7A8S43ryYdbWpJKeHRZRcq',
 '2sSGPbdZJkaSE2AbcGOACx',
 '6W9RUw7xnNRYtgh8dimg7L',
 '2wIVse2owClT7go1WT98tk',
 '69u5rPwWBKP7pJHpCGB9O5',
 '0kkxsdcaWmWU2yWAqclDh4',
 '2QWIScpFDNxmS6ZEMIUvgm',
 '5yy76ufVriyvidNSvXlRU1',
 '55Aa2cqylxrFIXC767Z865',
 '66jpZDjMcxF3SfDfwK7GXe',
 '4VMYDCV2IEDYJArk749S6m',
 '1GmsPCcpKgF9OhlNXjOsbS',
 '1svaANJTE5KrG16fTGDqOs',
 '2cPqdH7XMvwaBJEVjheH8g',
 '5pUo3fmmHT8bhCyHE52hA6',
 '5fahUm8t5c0GIdeTq0ZaG8',
 '7gP3bB2nilZXLfPHJhMdvc',
 '5TphiK6LsT4X5NOZxq3NJB',
 '1buzCmyYZE4kcdLRudsb8V',
 '3E6xrwgnVfYCrCs0ePERDz',
 

In [193]:
artists = []
for song in topsongs['artists']:
    if type(song) != float:
        for artist in song:
            artists.append(artist)
            
artists

[{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'},
 {'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'},
 {'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'},
 {'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'},
 {'246dkjvS1zLTtiykXe5h60': 'Post Malone'},
 {'1zNqQNIdeOUZHb8zbZRFMX': 'Swae Lee'},
 {'53XhwfbYqKCa1cC15pYq2q': 'Imagine Dragons'},
 {'2tIP7SsRs7vjIcLrU85W8J': 'The Kid LAROI'},
 {'1uNFoZAHBGtllmzznpCI3s': 'Justin Bieber'},
 {'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'},
 {'4yvcSjfu4PC0CYQyLy4wSq': 'Glass Animals'},
 {'6KImCVD70vtIoJWnq6nGn3': 'Harry Styles'},
 {'6qqNVTkY8uBg9cP3Jd7DAH': 'Billie Eilish'},
 {'6LuN9FCkKOj5PcnpouEgny': 'Khalid'},
 {'7n2wHs1TKAczGzO7Dd2rGr': 'Shawn Mendes'},
 {'4nDoRrQiYLoBzwC5BhVJzF': 'Camila Cabello'},
 {'246dkjvS1zLTtiykXe5h60': 'Post Malone'},
 {'1URnnhqYAYcrqrcwql10ft': '21 Savage'},
 {'6M2wZ9GZgrQXHCFfjv46we': 'Dua Lipa'},
 {'6qgnBH6iDM91ipVXv28OMu': 'KAYTRANADA'},
 {'6KImCVD70vtIoJWnq6nGn3': 'Harry Styles'},
 {'4IWBUUAFIplrNtaOHcJPRM': 'James Arthur'},
 {'2WGHW5rueHl3MmTMRl1UkS': 

In [ ]:
# # Creates a column for every value in the dictionary and returns true if that value shows up in genre_ids
# for i in range(listofallgenres):
#     topsongs[listofallgenres[i]] = \
#     (topsongs['artists'].map(lambda x: listofallgenres[i] in x))
# for i in range(len(genre_ids_dict)):
#     tmdbMovies[list(genre_ids_dict.values())[i]] = \
#     (tmdbMovies['genre_ids'].map(lambda x: list(genre_ids_dict.keys())[i] in x)).astype(int)

In [ ]:
songartists
topsongs

In [180]:
songartist = pd.DataFrame(columns = ['id','songid','artistid'])

In [181]:
# to create the song artist table (join table for songs and artists)
songartist = pd.DataFrame(columns = ['id','songid','artistid'])
tempdf = topsongs[['artists','songid']]
for song in tempdf.iterrows():
    # if not nan   
    if type(song[1][0]) != float:
        for artist in song[1][0]:
            songartist.loc[len(songartist.index)] = [len(songartist.index),song[1][1],list(artist.keys())[0]]
            

(0, artists    [{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}]
songid                         0VjIjW4GlUZAMYd2vXMi3b
Name: 0, dtype: object)
[{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}]
0VjIjW4GlUZAMYd2vXMi3b
(1, artists    [{'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}]
songid                         7qiZfU4dY1lWllzX7mPBI3
Name: 1, dtype: object)
[{'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}]
7qiZfU4dY1lWllzX7mPBI3
(2, artists    [{'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}]
songid                            7qEHsqek33rTcFNT9PFqLf
Name: 2, dtype: object)
[{'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}]
7qEHsqek33rTcFNT9PFqLf
(3, artists    [{'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}]
songid                          2XU0oxnq2qxCpomAAuJY8K
Name: 3, dtype: object)
[{'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}]
2XU0oxnq2qxCpomAAuJY8K
(4, artists    [{'246dkjvS1zLTtiykXe5h60': 'Post Malone'}, {'...
songid                                3KkXRkHbMCARz0aVfEt68P
Name: 4, dtype: object)
[{'246dkjvS1zLTtiykXe5h60': 'P

Name: 74, dtype: object)
[{'716NhGYqD1jl2wI1Qkgq36': 'Bizarrap'}, {'52iwsT98xCoGgiGntTiR7K': 'Quevedo'}]
2tTmW7RDtMQtBk7m2rYeSw
(75, artists    [{'04gDigrS5kc9YWfZHwBETP': 'Maroon 5'}]
songid                       27iLxkpPywM1Cep3RH7QWk
Name: 75, dtype: object)
[{'04gDigrS5kc9YWfZHwBETP': 'Maroon 5'}]
27iLxkpPywM1Cep3RH7QWk
(76, artists    [{'4O15NlyKLIASxsJ0PrXPfz': 'Lil Uzi Vert'}]
songid                           7GX5flRQZVHRAGd6B4TmDO
Name: 76, dtype: object)
[{'4O15NlyKLIASxsJ0PrXPfz': 'Lil Uzi Vert'}]
7GX5flRQZVHRAGd6B4TmDO
(77, artists    [{'2FXC3k01G6Gw61bmprjgqS': 'Hozier'}]
songid                     1CS7Sd1u5tWkstBhpssyjP
Name: 77, dtype: object)
[{'2FXC3k01G6Gw61bmprjgqS': 'Hozier'}]
1CS7Sd1u5tWkstBhpssyjP
(78, artists    [{'6qqNVTkY8uBg9cP3Jd7DAH': 'Billie Eilish'}]
songid                            43zdsphuZLzwA9k4DJhU0I
Name: 78, dtype: object)
[{'6qqNVTkY8uBg9cP3Jd7DAH': 'Billie Eilish'}]
43zdsphuZLzwA9k4DJhU0I
(79, artists    [{'15UsOTVnJzReFVN1VCnxy4': 'XXXTENTACION'}

Name: 133, dtype: object)
[{'6l3HvQ5sa6mXTsMTB19rO5': 'J. Cole'}]
68Dni7IE4VyPkTOH9mRWHr
(134, artists    [{'4V8Sr092TqfHkfAA5fXXqG': 'Luis Fonsi'}, {'4...
songid                                6habFhsOp2NvshLv26DqMb
Name: 134, dtype: object)
[{'4V8Sr092TqfHkfAA5fXXqG': 'Luis Fonsi'}, {'4VMYDCV2IEDYJArk749S6m': 'Daddy Yankee'}]
6habFhsOp2NvshLv26DqMb
(135, artists    [{'3MZsBdqDrRTJihTHQrO6Dq': 'Joji'}]
songid                   6xGruZOHLs39ZbVccQTuPZ
Name: 135, dtype: object)
[{'3MZsBdqDrRTJihTHQrO6Dq': 'Joji'}]
6xGruZOHLs39ZbVccQTuPZ
(136, artists    [{'45dkTj5sMRSjrmBSBeiHym': 'Tate McRae'}]
songid                         45bE4HXI0AwGZXfZtMp8JR
Name: 136, dtype: object)
[{'45dkTj5sMRSjrmBSBeiHym': 'Tate McRae'}]
45bE4HXI0AwGZXfZtMp8JR
(137, artists    [{'1Cs0zKBU1kc0i8ypK3B9ai': 'David Guetta'}, {...
songid                                4uUG5RXrOk84mYEfFvj3cK
Name: 137, dtype: object)
[{'1Cs0zKBU1kc0i8ypK3B9ai': 'David Guetta'}, {'64M6ah0SkkRsnPGtGiRAbb': 'Bebe Rexha'}]
4uUG5RXrOk84

(187, artists    [{'64M6ah0SkkRsnPGtGiRAbb': 'Bebe Rexha'}, {'3...
songid                                7iDa6hUg2VgEL1o1HjmfBn
Name: 187, dtype: object)
[{'64M6ah0SkkRsnPGtGiRAbb': 'Bebe Rexha'}, {'3b8QkneNDz4JHKKKlLgYZg': 'Florida Georgia Line'}]
7iDa6hUg2VgEL1o1HjmfBn
(188, artists    [{'4q3ewBCX7sLwd24euuV69X': 'Bad Bunny'}, {'3T...
songid                                3gE4eQH3K83Sght0ZLvuBK
Name: 188, dtype: object)
[{'4q3ewBCX7sLwd24euuV69X': 'Bad Bunny'}, {'3TVXtAsR1Inumwj472S9r4': 'Drake'}]
3gE4eQH3K83Sght0ZLvuBK
(189, artists    [{'4QVBYiagIaa6ZGSPMbybpy': 'Pedro Capó'}, {'3...
songid                                5iwz1NiezX7WWjnCgY5TH4
Name: 189, dtype: object)
[{'4QVBYiagIaa6ZGSPMbybpy': 'Pedro Capó'}, {'329e4yvIujISKGKz1BZZbO': 'Farruko'}]
5iwz1NiezX7WWjnCgY5TH4
(190, artists    [{'1uNFoZAHBGtllmzznpCI3s': 'Justin Bieber'}, ...
songid                                5CLagi4tXt2jLxBkU1IMfg
Name: 190, dtype: object)
[{'1uNFoZAHBGtllmzznpCI3s': 'Justin Bieber'}, {'0VRj0yCOv2F

(248, artists    [{'2qxJFvFYMEDqd7ui6kSAcq': 'Zedd'}, {'2wUjUUt...
songid                                6uBhi9gBXWjanegOb2Phh0
Name: 248, dtype: object)
[{'2qxJFvFYMEDqd7ui6kSAcq': 'Zedd'}, {'2wUjUUtkb5lvLKcGKsKqsR': 'Alessia Cara'}]
6uBhi9gBXWjanegOb2Phh0
(249, artists    [{'0C8ZW7ezQVs4URX5aX7Kqx': 'Selena Gomez'}, {...
songid                                0tBbt8CrmxbjRP0pueQkyU
Name: 249, dtype: object)
[{'0C8ZW7ezQVs4URX5aX7Kqx': 'Selena Gomez'}, {'64KEffDW9EtZ1y2vBYgq8T': 'Marshmello'}]
0tBbt8CrmxbjRP0pueQkyU
(250, artists    [{'2wY79sveU1sp5g7SokKOiI': 'Sam Smith'}]
songid                        5Nm9ERjJZ5oyfXZTECKmRt
Name: 250, dtype: object)
[{'2wY79sveU1sp5g7SokKOiI': 'Sam Smith'}]
5Nm9ERjJZ5oyfXZTECKmRt
(251, artists    [{'7Ln80lUS6He07XvHI8qqHH': 'Arctic Monkeys'}]
songid                             58ge6dfP91o9oXMzq3XkIS
Name: 251, dtype: object)
[{'7Ln80lUS6He07XvHI8qqHH': 'Arctic Monkeys'}]
58ge6dfP91o9oXMzq3XkIS
(252, artists    [{'1RyvyyTE3xzB2ZywiAwp0i': 'Future'}]
s

...

Name: 5950, dtype: object)
[{'2nuKjZLgc7II6FO4Rxjt5e': 'Blonde'}, {'2JyWXPbkqI5ZJa3gwqVa0c': 'Craig David'}]
4PFQ4EQBtJUp2jQjpmYkVA
(5951, artists    [{'02kJSzxNuaWGqwubyUba0Z': 'G-Eazy'}, {'0c173...
songid                                4wckW1OjAM2z6elKQdqUpi
Name: 5951, dtype: object)
[{'02kJSzxNuaWGqwubyUba0Z': 'G-Eazy'}, {'0c173mlxpT3dSFRgMO8XPh': 'Big Sean'}]
4wckW1OjAM2z6elKQdqUpi
(5952, artists    [{'0X2BH1fck6amBIoJhDVmmJ': 'Ellie Goulding'}]
songid                             3R2bkLqP197fl3vKHpONrg
Name: 5952, dtype: object)
[{'0X2BH1fck6amBIoJhDVmmJ': 'Ellie Goulding'}]
3R2bkLqP197fl3vKHpONrg
(5953, artists    [{'5pKCCKE2ajJHZ9KAiaK11H': 'Rihanna'}]
songid                      6K4Co1NQyOnoFEJMkZHkln
Name: 5953, dtype: object)
[{'5pKCCKE2ajJHZ9KAiaK11H': 'Rihanna'}]
6K4Co1NQyOnoFEJMkZHkln
(5954, artists    [{'3WrFJ7ztbogyGnTHbHJFl2': 'The Beatles'}]
songid                          4pbG9SUmWIvsROVLF0zF9s
Name: 5954, dtype: object)
[{'3WrFJ7ztbogyGnTHbHJFl2': 'The Beatles'}]
4pb

Name: 5998, dtype: object)
[{'00FQb4jTyendYWaN8pK0wa': 'Lana Del Rey'}]
3sYDVtqO35oRSOIMx7dOqR
(5999, artists    [{'0ZrpamOxcZybMHGg1AYtHP': 'Robin Thicke'}, {...
songid                                16e3Ly7ddGqqnFDiWWWwnc
Name: 5999, dtype: object)
[{'0ZrpamOxcZybMHGg1AYtHP': 'Robin Thicke'}, {'0hCNtLu0JehylgoiP8L4Gh': 'Nicki Minaj'}]
16e3Ly7ddGqqnFDiWWWwnc
(6000, artists    [{'5pZE9tgrhmIGWAsJZ7YxNK': 'Luny Tunes'}, {'4...
songid                                4777sGsOdoM89vPH3CVoLe
Name: 6000, dtype: object)
[{'5pZE9tgrhmIGWAsJZ7YxNK': 'Luny Tunes'}, {'4VMYDCV2IEDYJArk749S6m': 'Daddy Yankee'}, {'33ScadVnbm2X8kkUqOkC6Z': 'Don Omar'}, {'1wZtkThiXbVNtj6hee6dz9': 'Wisin & Yandel'}]
4777sGsOdoM89vPH3CVoLe
(6001, artists    [{'13ubrt8QOOCPljQ2FL1Kca': 'A$AP Rocky'}, {'2...
songid                                2N3U8uTYhjX2KwGT0pf5x0
Name: 6001, dtype: object)
[{'13ubrt8QOOCPljQ2FL1Kca': 'A$AP Rocky'}, {'2y8Jo9CKhJvtfeKOsYzRdT': 'Rod Stewart'}, {'360IAlyVv4PCEVjgyMZrxK': 'Miguel'}, {'3hv9

Name: 6049, dtype: object)
[{'2gsggkzM5R49q6jpPvazou': 'Jessie J'}]
4PYiIgzcp4o5pEYji1xY9q
(6050, artists    [{'3TVXtAsR1Inumwj472S9r4': 'Drake'}, {'3nFkdl...
songid                                4NVNapccSX7E5JLiW0uQEy
Name: 6050, dtype: object)
[{'3TVXtAsR1Inumwj472S9r4': 'Drake'}, {'3nFkdlSjzX9mRTtwJOzDYB': 'JAY-Z'}]
4NVNapccSX7E5JLiW0uQEy
(6051, artists    [{'4AK6F7OLvEQ5QYCBNiQWHq': 'One Direction'}]
songid                            23xx852ectQgmp1G78zSpd
Name: 6051, dtype: object)
[{'4AK6F7OLvEQ5QYCBNiQWHq': 'One Direction'}]
23xx852ectQgmp1G78zSpd
(6052, artists    [{'7EK1bQADBoqbYXnT4Cqv9w': 'John Denver'}]
songid                          3vXnnXluEiB3oc62q6QckE
Name: 6052, dtype: object)
[{'7EK1bQADBoqbYXnT4Cqv9w': 'John Denver'}]
3vXnnXluEiB3oc62q6QckE
(6053, artists    [{'3RqBeV12Tt7A8xH3zBDDUF': 'Kelsea Ballerini'}]
songid                               0knbW9EwgSLfNFMWys1mQm
Name: 6053, dtype: object)
[{'3RqBeV12Tt7A8xH3zBDDUF': 'Kelsea Ballerini'}]
0knbW9EwgSLfNFMWys1mQm
(

Name: 6097, dtype: object)
[{'4xFUf1FHVy696Q1JQZMTRj': 'Carrie Underwood'}]
10RQKVSr4rS0coExTmi4dF
(6098, artists    [{'1Cs0zKBU1kc0i8ypK3B9ai': 'David Guetta'}, {...
songid                                5b2bu6yyATC1zMXDGScJ2d
Name: 6098, dtype: object)
[{'1Cs0zKBU1kc0i8ypK3B9ai': 'David Guetta'}, {'4D75GcNG95ebPtNvoNVXhz': 'AFROJACK'}, {'64M6ah0SkkRsnPGtGiRAbb': 'Bebe Rexha'}, {'0hCNtLu0JehylgoiP8L4Gh': 'Nicki Minaj'}]
5b2bu6yyATC1zMXDGScJ2d
(6099, artists    [{'5yG7ZAZafVaAlMTeBybKAL': 'Iggy Azalea'}, {'...
songid                                7MQREx2p9bXdqm8WTGVkGI
Name: 6099, dtype: object)
[{'5yG7ZAZafVaAlMTeBybKAL': 'Iggy Azalea'}, {'0bdfiayQAKewqEvaU6rXCv': 'MØ'}]
7MQREx2p9bXdqm8WTGVkGI
(6100, artists    [{'7n2wHs1TKAczGzO7Dd2rGr': 'Shawn Mendes'}]
songid                           14hJ5tc1VCFMWhVn9axRTC
Name: 6100, dtype: object)
[{'7n2wHs1TKAczGzO7Dd2rGr': 'Shawn Mendes'}]
14hJ5tc1VCFMWhVn9axRTC
(6101, artists    [{'3QGKsAfhZdldQCLuLjk6zl': 'Us The Duo'}]
songid              

Name: 6141, dtype: object)
[{'7iW0o1suit8xY24m9M5L0u': 'De Vet Du'}]
70R0JGCHyprYZUxYkrKJIO
(6142, artists    [{'16GcWuvvybAoaHr0NqT8Eh': 'Alabama Shakes'}]
songid                             4gm6JpO3YOcogcjdtPqHWK
Name: 6142, dtype: object)
[{'16GcWuvvybAoaHr0NqT8Eh': 'Alabama Shakes'}]
4gm6JpO3YOcogcjdtPqHWK
(6143, artists    [{'2FXC3k01G6Gw61bmprjgqS': 'Hozier'}]
songid                     1C042FLYy7rP3MfnkOcnha
Name: 6143, dtype: object)
[{'2FXC3k01G6Gw61bmprjgqS': 'Hozier'}]
1C042FLYy7rP3MfnkOcnha
(6144, artists    [{'6PAt558ZEZl0DmdXlnjMgD': 'Eric Clapton'}, {...
songid                                618hiI74zBL8UVgAvfmkLj
Name: 6144, dtype: object)
[{'6PAt558ZEZl0DmdXlnjMgD': 'Eric Clapton'}, {'5xLSa7l4IV1gsQfhAMvl0U': 'B.B. King'}]
618hiI74zBL8UVgAvfmkLj
(6145, artists    [{'5xLSa7l4IV1gsQfhAMvl0U': 'B.B. King'}]
songid                        4NQfrmGs9iQXVQI9IpRhjM
Name: 6145, dtype: object)
[{'5xLSa7l4IV1gsQfhAMvl0U': 'B.B. King'}]
4NQfrmGs9iQXVQI9IpRhjM
(6146, artists    [{'4

In [182]:
songartist

id                  songid                artistid
0          0  0VjIjW4GlUZAMYd2vXMi3b  1Xyo4u8uXC1ZmMpatF05PJ
1          1  7qiZfU4dY1lWllzX7mPBI3  6eUKZXaKkcviH0Ku9w2n3V
2          2  7qEHsqek33rTcFNT9PFqLf  4GNC7GD6oZMSxPGyXy4MNB
3          3  2XU0oxnq2qxCpomAAuJY8K  2NjfBq1NflQcKSeiDooVjY
4          4  3KkXRkHbMCARz0aVfEt68P  246dkjvS1zLTtiykXe5h60
...      ...                     ...                     ...
10059  10059  3aeSTu6ejN2BU8YywEcHWO  360IAlyVv4PCEVjgyMZrxK
10060  10060  3KIzaWqMM6wjgVVfcfU5Uj  6Dy7Ex5zlTLgXbsB92rPji
10061  10061  3KIzaWqMM6wjgVVfcfU5Uj  2rRz9oFFpSHCpSTeUzthVI
10062  10062  3KIzaWqMM6wjgVVfcfU5Uj  0ONHkAv9pCAFxb0zJwDNTy
10063  10063  3YR1CSEZrjaCXdvyR1Uj8h  3IaqL9bsZtYJkqNLiovVho

[10064 rows x 3 columns]

In [220]:
artist = pd.DataFrame(columns = ['artistid','artistname'])
artist['temp'] = artists
list(artist['temp'][1].keys())[0]
list(artist['temp'][1].values())[0]
artist['artistid'] = artist.apply(lambda x: list(x['temp'].keys())[0], axis = 1)
artist['artistname'] = artist.apply(lambda x: list(x['temp'].values())[0], axis = 1)
artist = artist.drop_duplicates(['artistid'])
artist = artist.reset_index()
artist.drop('temp', axis = 1, inplace = True)
# topsongs['items'] = topsongs.apply(lambda x: x['info']['tracks']['items'], axis = 1)

In [221]:
artist

index                artistid          artistname
0         0  1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd
1         1  6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran
2         2  4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi
3         3  2NjfBq1NflQcKSeiDooVjY         Tones And I
4         4  246dkjvS1zLTtiykXe5h60         Post Malone
...     ...                     ...                 ...
2301  10053  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti
2302  10055  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell
2303  10060  6Dy7Ex5zlTLgXbsB92rPji                iSHi
2304  10061  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi
2305  10063  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost

[2306 rows x 3 columns]

In [218]:
artist = artist.drop_duplicates(['artistid'])
artist = artist.reset_index()

In [219]:
artist

index                artistid          artistname  \
0         0  1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd   
1         1  6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran   
2         2  4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi   
3         3  2NjfBq1NflQcKSeiDooVjY         Tones And I   
4         4  246dkjvS1zLTtiykXe5h60         Post Malone   
...     ...                     ...                 ...   
2301  10053  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti   
2302  10055  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell   
2303  10060  6Dy7Ex5zlTLgXbsB92rPji                iSHi   
2304  10061  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi   
2305  10063  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost   

                                                  temp  
0             {'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}  
1             {'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}  
2          {'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}  
3            {'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}  
4            {'246dkjvS1zLTtiykXe5h60': 'Post Malone'}  
...                                                ...  
2301  {'2A4QYjCRttLAzRU4OgchuA': 'Syke Montana Gotti'}  
2302         {'2vGaSKEDFsVPBgcnGxqlBN': 'Alex Newell'}  
2303                {'6Dy7Ex5zlTLgXbsB92rPji': 'iSHi'}  
2304             {'2rRz9oFFpSHCpSTeUzthVI': 'WHOiSHi'}  
2305      {'3IaqL9bsZtYJkqNLiovVho': 'Handsome Ghost'}  

[2306 rows x 4 columns]

Now that I have the song, songartist, and artist tables, I need to get more information for the song and artist tables. For the songs, I want the features, and for the artists, I want the associated genres

In [230]:
results = sp.search(q=f"artist:The Weeknd",type = 'artist', limit = 1)
results#['artist']['items']['genres']

{'artists': {'href': 'https://api.spotify.com/v1/search?query=artist%3AThe+Weeknd&type=artist&offset=0&limit=1',
  'items': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'},
    'followers': {'href': None, 'total': 61407159},
    'genres': ['canadian contemporary r&b', 'canadian pop', 'pop'],
    'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ',
    'id': '1Xyo4u8uXC1ZmMpatF05PJ',
    'images': [{'height': 640,
      'url': 'https://i.scdn.co/image/ab6761610000e5ebb5f9e28219c169fd4b9e8379',
      'width': 640},
     {'height': 320,
      'url': 'https://i.scdn.co/image/ab67616100005174b5f9e28219c169fd4b9e8379',
      'width': 320},
     {'height': 160,
      'url': 'https://i.scdn.co/image/ab6761610000f178b5f9e28219c169fd4b9e8379',
      'width': 160}],
    'name': 'The Weeknd',
    'popularity': 98,
    'type': 'artist',
    'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}],
  'limit': 1,
  'next': 'https://api.spotify.com/v1/s

In [234]:
artist['artistinfo'] = artist.apply(lambda x: sp.search(q=f"artist:{x['artistname']}",type = 'artist', limit = 1), axis = 1)

In [235]:
artist

index                artistid          artistname  \
0         0  1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd   
1         1  6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran   
2         2  4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi   
3         3  2NjfBq1NflQcKSeiDooVjY         Tones And I   
4         4  246dkjvS1zLTtiykXe5h60         Post Malone   
...     ...                     ...                 ...   
2301  10053  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti   
2302  10055  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell   
2303  10060  6Dy7Ex5zlTLgXbsB92rPji                iSHi   
2304  10061  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi   
2305  10063  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost   

                                             aritstinfo  
0     {'artists': {'href': 'https://api.spotify.com/...  
1     {'artists': {'href': 'https://api.spotify.com/...  
2     {'artists': {'href': 'https://api.spotify.com/...  
3     {'artists': {'href': 'https://api.spotify.com/...  
4     {'artists': {'href': 'https://api.spotify.com/...  
...                                                 ...  
2301  {'artists': {'href': 'https://api.spotify.com/...  
2302  {'artists': {'href': 'https://api.spotify.com/...  
2303  {'artists': {'href': 'https://api.spotify.com/...  
2304  {'artists': {'href': 'https://api.spotify.com/...  
2305  {'artists': {'href': 'https://api.spotify.com/...  

[2306 rows x 4 columns]

In [236]:
artist.drop('index', axis = 1, inplace = True)

In [237]:
artist

artistid          artistname  \
0     1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd   
1     6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran   
2     4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi   
3     2NjfBq1NflQcKSeiDooVjY         Tones And I   
4     246dkjvS1zLTtiykXe5h60         Post Malone   
...                      ...                 ...   
2301  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti   
2302  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell   
2303  6Dy7Ex5zlTLgXbsB92rPji                iSHi   
2304  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi   
2305  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost   

                                             aritstinfo  
0     {'artists': {'href': 'https://api.spotify.com/...  
1     {'artists': {'href': 'https://api.spotify.com/...  
2     {'artists': {'href': 'https://api.spotify.com/...  
3     {'artists': {'href': 'https://api.spotify.com/...  
4     {'artists': {'href': 'https://api.spotify.com/...  
...                                                 ...  
2301  {'artists': {'href': 'https://api.spotify.com/...  
2302  {'artists': {'href': 'https://api.spotify.com/...  
2303  {'artists': {'href': 'https://api.spotify.com/...  
2304  {'artists': {'href': 'https://api.spotify.com/...  
2305  {'artists': {'href': 'https://api.spotify.com/...  

[2306 rows x 3 columns]

In [244]:
artist['artistinfo'][1]

{'artists': {'href': 'https://api.spotify.com/v1/search?query=artist%3AEd+Sheeran&type=artist&offset=0&limit=1',
  'items': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/6eUKZXaKkcviH0Ku9w2n3V'},
    'followers': {'href': None, 'total': 110663355},
    'genres': ['pop', 'uk pop'],
    'href': 'https://api.spotify.com/v1/artists/6eUKZXaKkcviH0Ku9w2n3V',
    'id': '6eUKZXaKkcviH0Ku9w2n3V',
    'images': [{'height': 640,
      'url': 'https://i.scdn.co/image/ab6761610000e5eb9e690225ad4445530612ccc9',
      'width': 640},
     {'height': 320,
      'url': 'https://i.scdn.co/image/ab676161000051749e690225ad4445530612ccc9',
      'width': 320},
     {'height': 160,
      'url': 'https://i.scdn.co/image/ab6761610000f1789e690225ad4445530612ccc9',
      'width': 160}],
    'name': 'Ed Sheeran',
    'popularity': 92,
    'type': 'artist',
    'uri': 'spotify:artist:6eUKZXaKkcviH0Ku9w2n3V'}],
  'limit': 1,
  'next': 'https://api.spotify.com/v1/search?query=artist%3AEd+Sheeran&ty

In [242]:
artist = artist.rename(columns={'aritstinfo':'artistinfo'})

In [267]:
# artist['followers'] = topsongs.apply(lambda x: x['info']['tracks'], axis = 1)

In [248]:
artist['artistinfo'][1]['artists']['items'][0]

{'external_urls': {'spotify': 'https://open.spotify.com/artist/6eUKZXaKkcviH0Ku9w2n3V'},
 'followers': {'href': None, 'total': 110663355},
 'genres': ['pop', 'uk pop'],
 'href': 'https://api.spotify.com/v1/artists/6eUKZXaKkcviH0Ku9w2n3V',
 'id': '6eUKZXaKkcviH0Ku9w2n3V',
 'images': [{'height': 640,
   'url': 'https://i.scdn.co/image/ab6761610000e5eb9e690225ad4445530612ccc9',
   'width': 640},
  {'height': 320,
   'url': 'https://i.scdn.co/image/ab676161000051749e690225ad4445530612ccc9',
   'width': 320},
  {'height': 160,
   'url': 'https://i.scdn.co/image/ab6761610000f1789e690225ad4445530612ccc9',
   'width': 160}],
 'name': 'Ed Sheeran',
 'popularity': 92,
 'type': 'artist',
 'uri': 'spotify:artist:6eUKZXaKkcviH0Ku9w2n3V'}

In [278]:
artist['followers'] = \
artist.apply(lambda x: x['artistinfo']['artists']['items'][0]['followers']['total'] if len(x['artistinfo']['artists']['items']>0) else np.nan, axis = 1)

TypeError: '>' not supported between instances of 'list' and 'int'

In [264]:
artist['artistinfo'][0]['artists']['items'][0]['followers']['total']

61407159

In [265]:
artist[artist["artistinfo"]=={}]

KeyError: 'aritsts'

In [257]:
artist['artistinfo'].head(2000)

0       {'artists': {'href': 'https://api.spotify.com/...
1       {'artists': {'href': 'https://api.spotify.com/...
2       {'artists': {'href': 'https://api.spotify.com/...
3       {'artists': {'href': 'https://api.spotify.com/...
4       {'artists': {'href': 'https://api.spotify.com/...
                              ...                        
1995    {'artists': {'href': 'https://api.spotify.com/...
1996    {'artists': {'href': 'https://api.spotify.com/...
1997    {'artists': {'href': 'https://api.spotify.com/...
1998    {'artists': {'href': 'https://api.spotify.com/...
1999    {'artists': {'href': 'https://api.spotify.com/...
Name: artistinfo, Length: 2000, dtype: object

In [270]:
artist

artistid          artistname  \
0     1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd   
1     6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran   
2     4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi   
3     2NjfBq1NflQcKSeiDooVjY         Tones And I   
4     246dkjvS1zLTtiykXe5h60         Post Malone   
...                      ...                 ...   
2301  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti   
2302  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell   
2303  6Dy7Ex5zlTLgXbsB92rPji                iSHi   
2304  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi   
2305  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost   

                                             artistinfo  \
0     {'artists': {'href': 'https://api.spotify.com/...   
1     {'artists': {'href': 'https://api.spotify.com/...   
2     {'artists': {'href': 'https://api.spotify.com/...   
3     {'artists': {'href': 'https://api.spotify.com/...   
4     {'artists': {'href': 'https://api.spotify.com/...   
...                                                 ...   
2301  {'artists': {'href': 'https://api.spotify.com/...   
2302  {'artists': {'href': 'https://api.spotify.com/...   
2303  {'artists': {'href': 'https://api.spotify.com/...   
2304  {'artists': {'href': 'https://api.spotify.com/...   
2305  {'artists': {'href': 'https://api.spotify.com/...   

                                              followers  
0     [{'external_urls': {'spotify': 'https://open.s...  
1     [{'external_urls': {'spotify': 'https://open.s...  
2     [{'external_urls': {'spotify': 'https://open.s...  
3     [{'external_urls': {'spotify': 'https://open.s...  
4     [{'external_urls': {'spotify': 'https://open.s...  
...                                                 ...  
2301  [{'external_urls': {'spotify': 'https://open.s...  
2302  [{'external_urls': {'spotify': 'https://open.s...  
2303  [{'external_urls': {'spotify': 'https://open.s...  
2304  [{'external_urls': {'spotify': 'https://open.s...  
2305  [{'external_urls': {'spotify': 'https://open.s...  

[2306 rows x 4 columns]

In [266]:
for i in artist['artistinfo']:
    print(i)

{'artists': {'href': 'https://api.spotify.com/v1/search?query=artist%3AThe+Weeknd&type=artist&offset=0&limit=1', 'items': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'}, 'followers': {'href': None, 'total': 61407159}, 'genres': ['canadian contemporary r&b', 'canadian pop', 'pop'], 'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ', 'id': '1Xyo4u8uXC1ZmMpatF05PJ', 'images': [{'height': 640, 'url': 'https://i.scdn.co/image/ab6761610000e5ebb5f9e28219c169fd4b9e8379', 'width': 640}, {'height': 320, 'url': 'https://i.scdn.co/image/ab67616100005174b5f9e28219c169fd4b9e8379', 'width': 320}, {'height': 160, 'url': 'https://i.scdn.co/image/ab6761610000f178b5f9e28219c169fd4b9e8379', 'width': 160}], 'name': 'The Weeknd', 'popularity': 98, 'type': 'artist', 'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}], 'limit': 1, 'next': 'https://api.spotify.com/v1/search?query=artist%3AThe+Weeknd&type=artist&offset=1&limit=1', 'offset': 0, 'previous': 

In [275]:
artist[artist['artistinfo']=={}]

AttributeError: 'Series' object has no attribute 'artists'

In [2]:
artsit

NameError: name 'artsit' is not defined

In [8]:
topsongs

Pos             Artist                                          Title  \
0        1         The Weeknd                                Blinding Lights   
1        2         Ed Sheeran                                   Shape of You   
2        3      Lewis Capaldi                              Someone You Loved   
3        4        Tones And I                                   Dance Monkey   
4        5        Post Malone  Sunflower - Spider-Man: Into the Spider-Verse   
...    ...                ...                                            ...   
6175  6176       Mariah Carey                                       Infinity   
6176  6177  Twenty One Pilots                                   Fairly Local   
6177  6178           Ludacris                                     Good Lovin   
6178  6179               iSHi                                        Push It   
6179  6180     Handsome Ghost                                          Steps   

      Wks   T10   Pk   (x?)  PkStreams       Total  
0     172  64.0    1  (x13)   52375259  3406980588  
1     308  34.0    1  (x14)   64217796  3302350300  
2     218  15.0    4    NaN   24962682  2623186016  
3     151  41.0    1  (x17)   52055226  2538070349  
4     225  31.0    1   (x2)   34579416  2498983472  
...   ...   ...  ...    ...        ...         ...  
6175    1   NaN  220    NaN     177495      177495  
6176    1   NaN  234    NaN     176713      176713  
6177    1   NaN  223    NaN     174256      174256  
6178    1   NaN  236    NaN     173886      173886  
6179    1   NaN  239    NaN     166910      166910  

[6180 rows x 9 columns]

In [9]:
test = sp.search(q=f"track: \"{'Blinding Lights'}\" artist: \"{'The Weeknd'}\"", limit = 1)

In [13]:
test['tracks']['items'][0]['id']

'0VjIjW4GlUZAMYd2vXMi3b'

In [16]:
test_features = sp.audio_features('0VjIjW4GlUZAMYd2vXMi3b')

In [ ]:
featList = ['danceability','energy','key','loudness','mode','speechiness', 'acousticness', 'instrumentalness', 'liveness', 'valence', 'tempo','duration_ms', 'time_signature']
topsongs['features'] = topsongs.apply(lambda x: sp.audio_features(x['songid'])[0], axis = 1)
for feat in featList:
    topsongs[feat] = topsongs.apply(lambda x: x['features'][feat], axis = 1)

In [18]:
test_features[0]

{'danceability': 0.514,
 'energy': 0.73,
 'key': 1,
 'loudness': -5.934,
 'mode': 1,
 'speechiness': 0.0598,
 'acousticness': 0.00146,
 'instrumentalness': 9.54e-05,
 'liveness': 0.0897,
 'valence': 0.334,
 'tempo': 171.005,
 'type': 'audio_features',
 'id': '0VjIjW4GlUZAMYd2vXMi3b',
 'uri': 'spotify:track:0VjIjW4GlUZAMYd2vXMi3b',
 'track_href': 'https://api.spotify.com/v1/tracks/0VjIjW4GlUZAMYd2vXMi3b',
 'analysis_url': 'https://api.spotify.com/v1/audio-analysis/0VjIjW4GlUZAMYd2vXMi3b',
 'duration_ms': 200040,
 'time_signature': 4}

In [20]:
topsongs['items'] = topsongs.apply(lambda x: x['info']['tracks']['items'][0], axis = 1)

[{'album': {'album_group': 'album',
   'album_type': 'album',
   'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'},
     'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ',
     'id': '1Xyo4u8uXC1ZmMpatF05PJ',
     'name': 'The Weeknd',
     'type': 'artist',
     'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}],
   'available_markets': ['AD',
    'AE',
    'AG',
    'AL',
    'AM',
    'AO',
    'AR',
    'AT',
    'AU',
    'AZ',
    'BA',
    'BB',
    'BD',
    'BE',
    'BF',
    'BG',
    'BH',
    'BI',
    'BJ',
    'BN',
    'BO',
    'BR',
    'BS',
    'BT',
    'BW',
    'BY',
    'BZ',
    'CA',
    'CD',
    'CG',
    'CH',
    'CI',
    'CL',
    'CM',
    'CO',
    'CR',
    'CV',
    'CW',
    'CY',
    'CZ',
    'DE',
    'DJ',
    'DK',
    'DM',
    'DO',
    'DZ',
    'EC',
    'EE',
    'EG',
    'ES',
    'ET',
    'FI',
    'FJ',
    'FM',
    'FR',
    'GA',
    'GB',
    'GD',
    'GE',
    'GH

In [23]:
testinfo = test['tracks']['items'][0]

In [25]:
testinfo['id']

'0VjIjW4GlUZAMYd2vXMi3b'

In [ ]:
topsongs['songid'] = topsongs.apply(lambda x: x['items']['id'], axis = 1)

In [26]:
testinfo['popularity']

90

In [ ]:
topsongs['popularity'] = topsongs.apply(lambda x: x['items']['popularity'], axis = 1)

In [28]:
testinfo['explicit']

False

In [14]:
#view the types imported
topsongs.dtypes

Pos            int64
Artist        object
Title         object
Wks            int64
T10          float64
Pk             int64
(x?)          object
PkStreams      int64
Total          int64
info          object
dtype: object

In [18]:
#View the type of an element in the last column 
print(type(topsongs['info'][0]),topsongs['info'][0]) 


<class 'str'> {'tracks': {'href': 'https://api.spotify.com/v1/search?query=track%3A+%22Blinding+Lights%22+artist%3A+%22The+Weeknd%22&type=track&offset=0&limit=1', 'items': [{'album': {'album_group': 'album', 'album_type': 'album', 'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'}, 'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ', 'id': '1Xyo4u8uXC1ZmMpatF05PJ', 'name': 'The Weeknd', 'type': 'artist', 'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}], 'available_markets': ['AD', 'AE', 'AG', 'AL', 'AM', 'AO', 'AR', 'AT', 'AU', 'AZ', 'BA', 'BB', 'BD', 'BE', 'BF', 'BG', 'BH', 'BI', 'BJ', 'BN', 'BO', 'BR', 'BS', 'BT', 'BW', 'BY', 'BZ', 'CA', 'CD', 'CG', 'CH', 'CI', 'CL', 'CM', 'CO', 'CR', 'CV', 'CW', 'CY', 'CZ', 'DE', 'DJ', 'DK', 'DM', 'DO', 'DZ', 'EC', 'EE', 'EG', 'ES', 'FI', 'FJ', 'FM', 'FR', 'GA', 'GB', 'GD', 'GE', 'GH', 'GM', 'GN', 'GQ', 'GR', 'GT', 'GW', 'GY', 'HK', 'HN', 'HR', 'HT', 'HU', 'ID', 'IE', 'IL', 'IN', 'IQ',

In [22]:
# sadly, we need to convert these long nested dictionaries/lsits into the proper type :^(
import json
jsontest = topsongs['info'][0].replace('\'','\"')
# json = json.loads(topsongs['info'][0].replace('\'','\"'))
# print(len(jsontest))
jsontest

'{"tracks": {"href": "https://api.spotify.com/v1/search?query=track%3A+%22Blinding+Lights%22+artist%3A+%22The+Weeknd%22&type=track&offset=0&limit=1", "items": [{"album": {"album_group": "album", "album_type": "album", "artists": [{"external_urls": {"spotify": "https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ"}, "href": "https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ", "id": "1Xyo4u8uXC1ZmMpatF05PJ", "name": "The Weeknd", "type": "artist", "uri": "spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ"}], "available_markets": ["AD", "AE", "AG", "AL", "AM", "AO", "AR", "AT", "AU", "AZ", "BA", "BB", "BD", "BE", "BF", "BG", "BH", "BI", "BJ", "BN", "BO", "BR", "BS", "BT", "BW", "BY", "BZ", "CA", "CD", "CG", "CH", "CI", "CL", "CM", "CO", "CR", "CV", "CW", "CY", "CZ", "DE", "DJ", "DK", "DM", "DO", "DZ", "EC", "EE", "EG", "ES", "FI", "FJ", "FM", "FR", "GA", "GB", "GD", "GE", "GH", "GM", "GN", "GQ", "GR", "GT", "GW", "GY", "HK", "HN", "HR", "HT", "HU", "ID", "IE", "IL", "IN", "IQ", "IS", "IT", 

In [ ]:
topsongs['explicit'] = topsongs.apply(lambda x: x['items']['explicit'], axis = 1)#view the types imported
topsongs.dtypes

#View the type of an element in the last column 
print(type(topsongs['info'][0]),topsongs['info'][0]) 


# sadly, we need to convert these long nested dictionaries/lsits into the proper type :^(
import json
jsontest = topsongs['info'][0].replace('\'','\"')
# json = json.loads(topsongs['info'][0].replace('\'','\"'))
# print(len(jsontest))
jsontest

In [ ]:
for row in topsongs:
    print(row)
    #     results = sp.search(q=f"track: \"{title}\" artist: \"{artist}\"", limit = 1,)

In [ ]:
artist = topsongs[['Artist','Title']].loc[4][0]
title  = topsongs[['Artist','Title']].loc[4][1]
# results = sp.search(q=f"song: \"{title}\" artist: \"{artist}\"", limit = 1,)
results = sp.search(q=f"track: \"{title}\" artist: \"{artist}\"", limit = 1,)
# print(results) 
results
#spotify:track:7qiZfU4dY1lWllzX7mPBI3
# track_uri = results['tracks']['items'][0]['uri']
# results['tracks']['items'][0]['uri']

In [ ]:
results['tracks']['items']['artists']

In [ ]:
for i in results['tracks']['items']['artists']:
    print(f"name: {i['name']}, id: {i['id']}")

In [ ]:
BASE_URL = 'https://api.spotify.com/v1/'

In [ ]:
print(f'{artist}{title}')

In [ ]:
for idx, track in enumerate(results['tracks']['items']):
    print(idx, track['name'])

In [ ]:
#new row = 
# df['column']= df.apply(lambda x: sp.search(q=f"track: \"{x['Title']}\" artist: \"{x['Artist']}\"", limit = 1,)
# topsongs.assign(test=lambda x:"track: "+{x.Title})['test']
topsongs['test'] = topsongs.apply(lambda x: "track: "+ str({x['Title']}), axis = 1)

In [ ]:
topsongs

In [ ]:
topsongs['test'] = topsongs.apply(lambda x: "track: "+ str({x['Title']}), axis = 1)


spotify does NOT let you pull streaming numbers with its API. To obtain streaming data, one can webscrape it. In the interest of time, I will not be scraping this data. However, you can use POPULARITY: which takes into account total number of streams and the recency of those streams. Because we are discover how to make a hit NOW (and not 5 years ago), This metric may be more beneficial than total number of streams\n

The API also does not associate a song with a particular genre. That information is gotten from the artists information.

In [7]:
topsongs['info'] = topsongs.apply(lambda x: sp.search(q=f"track: \"{x['Title']}\" artist: \"{x['Artist']}\"", limit = 1), axis = 1)

In [8]:
topsongs

Pos             Artist                                          Title  \
0        1         The Weeknd                                Blinding Lights   
1        2         Ed Sheeran                                   Shape of You   
2        3      Lewis Capaldi                              Someone You Loved   
3        4        Tones And I                                   Dance Monkey   
4        5        Post Malone  Sunflower - Spider-Man: Into the Spider-Verse   
...    ...                ...                                            ...   
6175  6176       Mariah Carey                                       Infinity   
6176  6177  Twenty One Pilots                                   Fairly Local   
6177  6178           Ludacris                                     Good Lovin   
6178  6179               iSHi                                        Push It   
6179  6180     Handsome Ghost                                          Steps   

      Wks   T10   Pk   (x?)  PkStreams       Total  \
0     172  64.0    1  (x13)   52375259  3406980588   
1     308  34.0    1  (x14)   64217796  3302350300   
2     218  15.0    4    NaN   24962682  2623186016   
3     151  41.0    1  (x17)   52055226  2538070349   
4     225  31.0    1   (x2)   34579416  2498983472   
...   ...   ...  ...    ...        ...         ...   
6175    1   NaN  220    NaN     177495      177495   
6176    1   NaN  234    NaN     176713      176713   
6177    1   NaN  223    NaN     174256      174256   
6178    1   NaN  236    NaN     173886      173886   
6179    1   NaN  239    NaN     166910      166910   

                                                   info  
0     {'tracks': {'href': 'https://api.spotify.com/v...  
1     {'tracks': {'href': 'https://api.spotify.com/v...  
2     {'tracks': {'href': 'https://api.spotify.com/v...  
3     {'tracks': {'href': 'https://api.spotify.com/v...  
4     {'tracks': {'href': 'https://api.spotify.com/v...  
...                                                 ...  
6175  {'tracks': {'href': 'https://api.spotify.com/v...  
6176  {'tracks': {'href': 'https://api.spotify.com/v...  
6177  {'tracks': {'href': 'https://api.spotify.com/v...  
6178  {'tracks': {'href': 'https://api.spotify.com/v...  
6179  {'tracks': {'href': 'https://api.spotify.com/v...  

[6180 rows x 10 columns]

In [9]:
topsongs.to_csv('Data/spotifyTopSongsWithAPI.tsv')

In [18]:
topsongs['info'][0]['tracks']['items']

[{'album': {'album_group': 'album',
   'album_type': 'album',
   'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'},
     'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ',
     'id': '1Xyo4u8uXC1ZmMpatF05PJ',
     'name': 'The Weeknd',
     'type': 'artist',
     'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}],
   'available_markets': ['AD',
    'AE',
    'AG',
    'AL',
    'AM',
    'AO',
    'AR',
    'AT',
    'AU',
    'AZ',
    'BA',
    'BB',
    'BD',
    'BE',
    'BF',
    'BG',
    'BH',
    'BI',
    'BJ',
    'BN',
    'BO',
    'BR',
    'BS',
    'BT',
    'BW',
    'BY',
    'BZ',
    'CA',
    'CD',
    'CG',
    'CH',
    'CI',
    'CL',
    'CM',
    'CO',
    'CR',
    'CV',
    'CW',
    'CY',
    'CZ',
    'DE',
    'DJ',
    'DK',
    'DM',
    'DO',
    'DZ',
    'EC',
    'EE',
    'EG',
    'ES',
    'FI',
    'FJ',
    'FM',
    'FR',
    'GA',
    'GB',
    'GD',
    'GE',
    'GH',
    'GM

In [20]:
topsongs['items'] = topsongs.apply(lambda x: x['info']['tracks']['items'], axis = 1)

In [25]:
topsongs['items']

[{'album': {'album_group': 'album',
   'album_type': 'album',
   'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/6eUKZXaKkcviH0Ku9w2n3V'},
     'href': 'https://api.spotify.com/v1/artists/6eUKZXaKkcviH0Ku9w2n3V',
     'id': '6eUKZXaKkcviH0Ku9w2n3V',
     'name': 'Ed Sheeran',
     'type': 'artist',
     'uri': 'spotify:artist:6eUKZXaKkcviH0Ku9w2n3V'}],
   'available_markets': ['AD',
    'AE',
    'AG',
    'AL',
    'AM',
    'AO',
    'AR',
    'AT',
    'AU',
    'AZ',
    'BA',
    'BB',
    'BD',
    'BE',
    'BF',
    'BG',
    'BH',
    'BI',
    'BJ',
    'BN',
    'BO',
    'BR',
    'BS',
    'BT',
    'BW',
    'BY',
    'BZ',
    'CA',
    'CD',
    'CG',
    'CH',
    'CI',
    'CL',
    'CM',
    'CO',
    'CR',
    'CV',
    'CW',
    'CY',
    'CZ',
    'DE',
    'DJ',
    'DK',
    'DM',
    'DO',
    'DZ',
    'EC',
    'EE',
    'EG',
    'ES',
    'ET',
    'FI',
    'FJ',
    'FM',
    'FR',
    'GA',
    'GB',
    'GD',
    'GE',
    'GH

In [29]:
topsongs[topsongs["items"].str.len() == 0]

Pos          Artist    Title  Wks  T10   Pk (x?)  PkStreams    Total  \
5283  5284  Samir & Viktor  Groupie    4  NaN  146  NaN    1469139  4955784   

                                                   info items  
5283  {'tracks': {'href': 'https://api.spotify.com/v...    []

The only song in this list that the query could not find is Groupie by Samir & Viktor. Upon further investigation, this song is undiscoverable because it is unvailable in my current region

In [27]:
sp.search(q=f"track: \"asdfasdfa\" artist: \"sadsjlkgdahgadh\"", limit = 1,)['tracks']['items']

[]

In [44]:
topsongs['items'][1][0]['artists'][0]

{'external_urls': {'spotify': 'https://open.spotify.com/artist/6eUKZXaKkcviH0Ku9w2n3V'},
 'href': 'https://api.spotify.com/v1/artists/6eUKZXaKkcviH0Ku9w2n3V',
 'id': '6eUKZXaKkcviH0Ku9w2n3V',
 'name': 'Ed Sheeran',
 'type': 'artist',
 'uri': 'spotify:artist:6eUKZXaKkcviH0Ku9w2n3V'}

In [ ]:
# topsongs['items'][rowindex][0]['artists'][artistindex]['id']
topsongs['items'][1][0]['artists'][0]['id']

In [ ]:
topsongs['artists']= 

In [49]:
for artist in topsongs['items'][0][0]['artists']:
    print(artist['id'])

1Xyo4u8uXC1ZmMpatF05PJ


In [112]:
topsongs['artists'] = topsongs.apply(lambda x: [{i['id']:i['name']}for i in x['items'][0]['artists']] if len(x['items']) != 0 else np.nan, axis = 1)

In [113]:
topsongs['items'][0][0]['artists']

[{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'},
  'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ',
  'id': '1Xyo4u8uXC1ZmMpatF05PJ',
  'name': 'The Weeknd',
  'type': 'artist',
  'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}]

In [114]:
topsongs['artists']

0              [{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}]
1              [{'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}]
2           [{'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}]
3             [{'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}]
4       [{'246dkjvS1zLTtiykXe5h60': 'Post Malone'}, {'...
                              ...                        
6175         [{'4iHNK0tOyZPYnBU7nGAgpQ': 'Mariah Carey'}]
6176    [{'3YQKmKGau1PzlVlkL1iodx': 'Twenty One Pilots'}]
6177    [{'3ipn9JLAPI5GUEo4y4jcoi': 'Ludacris'}, {'360...
6178    [{'6Dy7Ex5zlTLgXbsB92rPji': 'iSHi'}, {'2rRz9oF...
6179       [{'3IaqL9bsZtYJkqNLiovVho': 'Handsome Ghost'}]
Name: artists, Length: 6180, dtype: object

In [191]:
# topsongs['artists']
artists = set()
for song in topsongs['artists']:
    if type(song) != float:
        for artist in song:
            keys =list(artist.keys()) 
            artists.add(keys[0])
artists

{'1aQbanZ6xPrOtTYtsMdm3Q',
 '1U1el3k54VvEUzo3ybLPlM',
 '5j21TGkrNEAJe3gG9VlS34',
 '6xHUXzrfhFgnIv86EBR3Ml',
 '2nm38smINjms1LtczR0Cei',
 '3hPPNy5OBzCU1icQO7Nrok',
 '6VuMaDnrHyPL1p4EHjYLi7',
 '5wTdspmxzb8V4ZjvDodpBo',
 '5NW2uPFatEKjZQ5gpWD8HO',
 '0pePYDrJGk8gqMRbXrLJC8',
 '3ATyg4fGC9F8trfb0GRWmX',
 '3Oim8XBPbznAa8Jj8QzNc8',
 '3aQeKQSyrW4qWr35idm0cy',
 '3uwAm6vQy7kWPS2bciKWx9',
 '7jy3rLJdDQY21OgRLCZ9sD',
 '12vb80Km0Ew53ABfJOepVz',
 '3p3jPcp8b7WL9XYj4xlsWj',
 '7A8S43ryYdbWpJKeHRZRcq',
 '2sSGPbdZJkaSE2AbcGOACx',
 '6W9RUw7xnNRYtgh8dimg7L',
 '2wIVse2owClT7go1WT98tk',
 '69u5rPwWBKP7pJHpCGB9O5',
 '0kkxsdcaWmWU2yWAqclDh4',
 '2QWIScpFDNxmS6ZEMIUvgm',
 '5yy76ufVriyvidNSvXlRU1',
 '55Aa2cqylxrFIXC767Z865',
 '66jpZDjMcxF3SfDfwK7GXe',
 '4VMYDCV2IEDYJArk749S6m',
 '1GmsPCcpKgF9OhlNXjOsbS',
 '1svaANJTE5KrG16fTGDqOs',
 '2cPqdH7XMvwaBJEVjheH8g',
 '5pUo3fmmHT8bhCyHE52hA6',
 '5fahUm8t5c0GIdeTq0ZaG8',
 '7gP3bB2nilZXLfPHJhMdvc',
 '5TphiK6LsT4X5NOZxq3NJB',
 '1buzCmyYZE4kcdLRudsb8V',
 '3E6xrwgnVfYCrCs0ePERDz',
 

In [193]:
artists = []
for song in topsongs['artists']:
    if type(song) != float:
        for artist in song:
            artists.append(artist)
            
artists

[{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'},
 {'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'},
 {'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'},
 {'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'},
 {'246dkjvS1zLTtiykXe5h60': 'Post Malone'},
 {'1zNqQNIdeOUZHb8zbZRFMX': 'Swae Lee'},
 {'53XhwfbYqKCa1cC15pYq2q': 'Imagine Dragons'},
 {'2tIP7SsRs7vjIcLrU85W8J': 'The Kid LAROI'},
 {'1uNFoZAHBGtllmzznpCI3s': 'Justin Bieber'},
 {'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'},
 {'4yvcSjfu4PC0CYQyLy4wSq': 'Glass Animals'},
 {'6KImCVD70vtIoJWnq6nGn3': 'Harry Styles'},
 {'6qqNVTkY8uBg9cP3Jd7DAH': 'Billie Eilish'},
 {'6LuN9FCkKOj5PcnpouEgny': 'Khalid'},
 {'7n2wHs1TKAczGzO7Dd2rGr': 'Shawn Mendes'},
 {'4nDoRrQiYLoBzwC5BhVJzF': 'Camila Cabello'},
 {'246dkjvS1zLTtiykXe5h60': 'Post Malone'},
 {'1URnnhqYAYcrqrcwql10ft': '21 Savage'},
 {'6M2wZ9GZgrQXHCFfjv46we': 'Dua Lipa'},
 {'6qgnBH6iDM91ipVXv28OMu': 'KAYTRANADA'},
 {'6KImCVD70vtIoJWnq6nGn3': 'Harry Styles'},
 {'4IWBUUAFIplrNtaOHcJPRM': 'James Arthur'},
 {'2WGHW5rueHl3MmTMRl1UkS': 

In [ ]:
# # Creates a column for every value in the dictionary and returns true if that value shows up in genre_ids
# for i in range(listofallgenres):
#     topsongs[listofallgenres[i]] = \
#     (topsongs['artists'].map(lambda x: listofallgenres[i] in x))
# for i in range(len(genre_ids_dict)):
#     tmdbMovies[list(genre_ids_dict.values())[i]] = \
#     (tmdbMovies['genre_ids'].map(lambda x: list(genre_ids_dict.keys())[i] in x)).astype(int)

In [ ]:
songartists
topsongs

In [180]:
songartist = pd.DataFrame(columns = ['id','songid','artistid'])

In [181]:
# to create the song artist table (join table for songs and artists)
songartist = pd.DataFrame(columns = ['id','songid','artistid'])
tempdf = topsongs[['artists','songid']]
for song in tempdf.iterrows():
    # if not nan   
    if type(song[1][0]) != float:
        for artist in song[1][0]:
            songartist.loc[len(songartist.index)] = [len(songartist.index),song[1][1],list(artist.keys())[0]]
            

(0, artists    [{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}]
songid                         0VjIjW4GlUZAMYd2vXMi3b
Name: 0, dtype: object)
[{'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}]
0VjIjW4GlUZAMYd2vXMi3b
(1, artists    [{'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}]
songid                         7qiZfU4dY1lWllzX7mPBI3
Name: 1, dtype: object)
[{'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}]
7qiZfU4dY1lWllzX7mPBI3
(2, artists    [{'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}]
songid                            7qEHsqek33rTcFNT9PFqLf
Name: 2, dtype: object)
[{'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}]
7qEHsqek33rTcFNT9PFqLf
(3, artists    [{'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}]
songid                          2XU0oxnq2qxCpomAAuJY8K
Name: 3, dtype: object)
[{'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}]
2XU0oxnq2qxCpomAAuJY8K
(4, artists    [{'246dkjvS1zLTtiykXe5h60': 'Post Malone'}, {'...
songid                                3KkXRkHbMCARz0aVfEt68P
Name: 4, dtype: object)
[{'246dkjvS1zLTtiykXe5h60': 'P

Name: 74, dtype: object)
[{'716NhGYqD1jl2wI1Qkgq36': 'Bizarrap'}, {'52iwsT98xCoGgiGntTiR7K': 'Quevedo'}]
2tTmW7RDtMQtBk7m2rYeSw
(75, artists    [{'04gDigrS5kc9YWfZHwBETP': 'Maroon 5'}]
songid                       27iLxkpPywM1Cep3RH7QWk
Name: 75, dtype: object)
[{'04gDigrS5kc9YWfZHwBETP': 'Maroon 5'}]
27iLxkpPywM1Cep3RH7QWk
(76, artists    [{'4O15NlyKLIASxsJ0PrXPfz': 'Lil Uzi Vert'}]
songid                           7GX5flRQZVHRAGd6B4TmDO
Name: 76, dtype: object)
[{'4O15NlyKLIASxsJ0PrXPfz': 'Lil Uzi Vert'}]
7GX5flRQZVHRAGd6B4TmDO
(77, artists    [{'2FXC3k01G6Gw61bmprjgqS': 'Hozier'}]
songid                     1CS7Sd1u5tWkstBhpssyjP
Name: 77, dtype: object)
[{'2FXC3k01G6Gw61bmprjgqS': 'Hozier'}]
1CS7Sd1u5tWkstBhpssyjP
(78, artists    [{'6qqNVTkY8uBg9cP3Jd7DAH': 'Billie Eilish'}]
songid                            43zdsphuZLzwA9k4DJhU0I
Name: 78, dtype: object)
[{'6qqNVTkY8uBg9cP3Jd7DAH': 'Billie Eilish'}]
43zdsphuZLzwA9k4DJhU0I
(79, artists    [{'15UsOTVnJzReFVN1VCnxy4': 'XXXTENTACION'}

Name: 133, dtype: object)
[{'6l3HvQ5sa6mXTsMTB19rO5': 'J. Cole'}]
68Dni7IE4VyPkTOH9mRWHr
(134, artists    [{'4V8Sr092TqfHkfAA5fXXqG': 'Luis Fonsi'}, {'4...
songid                                6habFhsOp2NvshLv26DqMb
Name: 134, dtype: object)
[{'4V8Sr092TqfHkfAA5fXXqG': 'Luis Fonsi'}, {'4VMYDCV2IEDYJArk749S6m': 'Daddy Yankee'}]
6habFhsOp2NvshLv26DqMb
(135, artists    [{'3MZsBdqDrRTJihTHQrO6Dq': 'Joji'}]
songid                   6xGruZOHLs39ZbVccQTuPZ
Name: 135, dtype: object)
[{'3MZsBdqDrRTJihTHQrO6Dq': 'Joji'}]
6xGruZOHLs39ZbVccQTuPZ
(136, artists    [{'45dkTj5sMRSjrmBSBeiHym': 'Tate McRae'}]
songid                         45bE4HXI0AwGZXfZtMp8JR
Name: 136, dtype: object)
[{'45dkTj5sMRSjrmBSBeiHym': 'Tate McRae'}]
45bE4HXI0AwGZXfZtMp8JR
(137, artists    [{'1Cs0zKBU1kc0i8ypK3B9ai': 'David Guetta'}, {...
songid                                4uUG5RXrOk84mYEfFvj3cK
Name: 137, dtype: object)
[{'1Cs0zKBU1kc0i8ypK3B9ai': 'David Guetta'}, {'64M6ah0SkkRsnPGtGiRAbb': 'Bebe Rexha'}]
4uUG5RXrOk84

(187, artists    [{'64M6ah0SkkRsnPGtGiRAbb': 'Bebe Rexha'}, {'3...
songid                                7iDa6hUg2VgEL1o1HjmfBn
Name: 187, dtype: object)
[{'64M6ah0SkkRsnPGtGiRAbb': 'Bebe Rexha'}, {'3b8QkneNDz4JHKKKlLgYZg': 'Florida Georgia Line'}]
7iDa6hUg2VgEL1o1HjmfBn
(188, artists    [{'4q3ewBCX7sLwd24euuV69X': 'Bad Bunny'}, {'3T...
songid                                3gE4eQH3K83Sght0ZLvuBK
Name: 188, dtype: object)
[{'4q3ewBCX7sLwd24euuV69X': 'Bad Bunny'}, {'3TVXtAsR1Inumwj472S9r4': 'Drake'}]
3gE4eQH3K83Sght0ZLvuBK
(189, artists    [{'4QVBYiagIaa6ZGSPMbybpy': 'Pedro Capó'}, {'3...
songid                                5iwz1NiezX7WWjnCgY5TH4
Name: 189, dtype: object)
[{'4QVBYiagIaa6ZGSPMbybpy': 'Pedro Capó'}, {'329e4yvIujISKGKz1BZZbO': 'Farruko'}]
5iwz1NiezX7WWjnCgY5TH4
(190, artists    [{'1uNFoZAHBGtllmzznpCI3s': 'Justin Bieber'}, ...
songid                                5CLagi4tXt2jLxBkU1IMfg
Name: 190, dtype: object)
[{'1uNFoZAHBGtllmzznpCI3s': 'Justin Bieber'}, {'0VRj0yCOv2F

(248, artists    [{'2qxJFvFYMEDqd7ui6kSAcq': 'Zedd'}, {'2wUjUUt...
songid                                6uBhi9gBXWjanegOb2Phh0
Name: 248, dtype: object)
[{'2qxJFvFYMEDqd7ui6kSAcq': 'Zedd'}, {'2wUjUUtkb5lvLKcGKsKqsR': 'Alessia Cara'}]
6uBhi9gBXWjanegOb2Phh0
(249, artists    [{'0C8ZW7ezQVs4URX5aX7Kqx': 'Selena Gomez'}, {...
songid                                0tBbt8CrmxbjRP0pueQkyU
Name: 249, dtype: object)
[{'0C8ZW7ezQVs4URX5aX7Kqx': 'Selena Gomez'}, {'64KEffDW9EtZ1y2vBYgq8T': 'Marshmello'}]
0tBbt8CrmxbjRP0pueQkyU
(250, artists    [{'2wY79sveU1sp5g7SokKOiI': 'Sam Smith'}]
songid                        5Nm9ERjJZ5oyfXZTECKmRt
Name: 250, dtype: object)
[{'2wY79sveU1sp5g7SokKOiI': 'Sam Smith'}]
5Nm9ERjJZ5oyfXZTECKmRt
(251, artists    [{'7Ln80lUS6He07XvHI8qqHH': 'Arctic Monkeys'}]
songid                             58ge6dfP91o9oXMzq3XkIS
Name: 251, dtype: object)
[{'7Ln80lUS6He07XvHI8qqHH': 'Arctic Monkeys'}]
58ge6dfP91o9oXMzq3XkIS
(252, artists    [{'1RyvyyTE3xzB2ZywiAwp0i': 'Future'}]
s

...

Name: 5950, dtype: object)
[{'2nuKjZLgc7II6FO4Rxjt5e': 'Blonde'}, {'2JyWXPbkqI5ZJa3gwqVa0c': 'Craig David'}]
4PFQ4EQBtJUp2jQjpmYkVA
(5951, artists    [{'02kJSzxNuaWGqwubyUba0Z': 'G-Eazy'}, {'0c173...
songid                                4wckW1OjAM2z6elKQdqUpi
Name: 5951, dtype: object)
[{'02kJSzxNuaWGqwubyUba0Z': 'G-Eazy'}, {'0c173mlxpT3dSFRgMO8XPh': 'Big Sean'}]
4wckW1OjAM2z6elKQdqUpi
(5952, artists    [{'0X2BH1fck6amBIoJhDVmmJ': 'Ellie Goulding'}]
songid                             3R2bkLqP197fl3vKHpONrg
Name: 5952, dtype: object)
[{'0X2BH1fck6amBIoJhDVmmJ': 'Ellie Goulding'}]
3R2bkLqP197fl3vKHpONrg
(5953, artists    [{'5pKCCKE2ajJHZ9KAiaK11H': 'Rihanna'}]
songid                      6K4Co1NQyOnoFEJMkZHkln
Name: 5953, dtype: object)
[{'5pKCCKE2ajJHZ9KAiaK11H': 'Rihanna'}]
6K4Co1NQyOnoFEJMkZHkln
(5954, artists    [{'3WrFJ7ztbogyGnTHbHJFl2': 'The Beatles'}]
songid                          4pbG9SUmWIvsROVLF0zF9s
Name: 5954, dtype: object)
[{'3WrFJ7ztbogyGnTHbHJFl2': 'The Beatles'}]
4pb

Name: 5998, dtype: object)
[{'00FQb4jTyendYWaN8pK0wa': 'Lana Del Rey'}]
3sYDVtqO35oRSOIMx7dOqR
(5999, artists    [{'0ZrpamOxcZybMHGg1AYtHP': 'Robin Thicke'}, {...
songid                                16e3Ly7ddGqqnFDiWWWwnc
Name: 5999, dtype: object)
[{'0ZrpamOxcZybMHGg1AYtHP': 'Robin Thicke'}, {'0hCNtLu0JehylgoiP8L4Gh': 'Nicki Minaj'}]
16e3Ly7ddGqqnFDiWWWwnc
(6000, artists    [{'5pZE9tgrhmIGWAsJZ7YxNK': 'Luny Tunes'}, {'4...
songid                                4777sGsOdoM89vPH3CVoLe
Name: 6000, dtype: object)
[{'5pZE9tgrhmIGWAsJZ7YxNK': 'Luny Tunes'}, {'4VMYDCV2IEDYJArk749S6m': 'Daddy Yankee'}, {'33ScadVnbm2X8kkUqOkC6Z': 'Don Omar'}, {'1wZtkThiXbVNtj6hee6dz9': 'Wisin & Yandel'}]
4777sGsOdoM89vPH3CVoLe
(6001, artists    [{'13ubrt8QOOCPljQ2FL1Kca': 'A$AP Rocky'}, {'2...
songid                                2N3U8uTYhjX2KwGT0pf5x0
Name: 6001, dtype: object)
[{'13ubrt8QOOCPljQ2FL1Kca': 'A$AP Rocky'}, {'2y8Jo9CKhJvtfeKOsYzRdT': 'Rod Stewart'}, {'360IAlyVv4PCEVjgyMZrxK': 'Miguel'}, {'3hv9

Name: 6049, dtype: object)
[{'2gsggkzM5R49q6jpPvazou': 'Jessie J'}]
4PYiIgzcp4o5pEYji1xY9q
(6050, artists    [{'3TVXtAsR1Inumwj472S9r4': 'Drake'}, {'3nFkdl...
songid                                4NVNapccSX7E5JLiW0uQEy
Name: 6050, dtype: object)
[{'3TVXtAsR1Inumwj472S9r4': 'Drake'}, {'3nFkdlSjzX9mRTtwJOzDYB': 'JAY-Z'}]
4NVNapccSX7E5JLiW0uQEy
(6051, artists    [{'4AK6F7OLvEQ5QYCBNiQWHq': 'One Direction'}]
songid                            23xx852ectQgmp1G78zSpd
Name: 6051, dtype: object)
[{'4AK6F7OLvEQ5QYCBNiQWHq': 'One Direction'}]
23xx852ectQgmp1G78zSpd
(6052, artists    [{'7EK1bQADBoqbYXnT4Cqv9w': 'John Denver'}]
songid                          3vXnnXluEiB3oc62q6QckE
Name: 6052, dtype: object)
[{'7EK1bQADBoqbYXnT4Cqv9w': 'John Denver'}]
3vXnnXluEiB3oc62q6QckE
(6053, artists    [{'3RqBeV12Tt7A8xH3zBDDUF': 'Kelsea Ballerini'}]
songid                               0knbW9EwgSLfNFMWys1mQm
Name: 6053, dtype: object)
[{'3RqBeV12Tt7A8xH3zBDDUF': 'Kelsea Ballerini'}]
0knbW9EwgSLfNFMWys1mQm
(

Name: 6097, dtype: object)
[{'4xFUf1FHVy696Q1JQZMTRj': 'Carrie Underwood'}]
10RQKVSr4rS0coExTmi4dF
(6098, artists    [{'1Cs0zKBU1kc0i8ypK3B9ai': 'David Guetta'}, {...
songid                                5b2bu6yyATC1zMXDGScJ2d
Name: 6098, dtype: object)
[{'1Cs0zKBU1kc0i8ypK3B9ai': 'David Guetta'}, {'4D75GcNG95ebPtNvoNVXhz': 'AFROJACK'}, {'64M6ah0SkkRsnPGtGiRAbb': 'Bebe Rexha'}, {'0hCNtLu0JehylgoiP8L4Gh': 'Nicki Minaj'}]
5b2bu6yyATC1zMXDGScJ2d
(6099, artists    [{'5yG7ZAZafVaAlMTeBybKAL': 'Iggy Azalea'}, {'...
songid                                7MQREx2p9bXdqm8WTGVkGI
Name: 6099, dtype: object)
[{'5yG7ZAZafVaAlMTeBybKAL': 'Iggy Azalea'}, {'0bdfiayQAKewqEvaU6rXCv': 'MØ'}]
7MQREx2p9bXdqm8WTGVkGI
(6100, artists    [{'7n2wHs1TKAczGzO7Dd2rGr': 'Shawn Mendes'}]
songid                           14hJ5tc1VCFMWhVn9axRTC
Name: 6100, dtype: object)
[{'7n2wHs1TKAczGzO7Dd2rGr': 'Shawn Mendes'}]
14hJ5tc1VCFMWhVn9axRTC
(6101, artists    [{'3QGKsAfhZdldQCLuLjk6zl': 'Us The Duo'}]
songid              

Name: 6141, dtype: object)
[{'7iW0o1suit8xY24m9M5L0u': 'De Vet Du'}]
70R0JGCHyprYZUxYkrKJIO
(6142, artists    [{'16GcWuvvybAoaHr0NqT8Eh': 'Alabama Shakes'}]
songid                             4gm6JpO3YOcogcjdtPqHWK
Name: 6142, dtype: object)
[{'16GcWuvvybAoaHr0NqT8Eh': 'Alabama Shakes'}]
4gm6JpO3YOcogcjdtPqHWK
(6143, artists    [{'2FXC3k01G6Gw61bmprjgqS': 'Hozier'}]
songid                     1C042FLYy7rP3MfnkOcnha
Name: 6143, dtype: object)
[{'2FXC3k01G6Gw61bmprjgqS': 'Hozier'}]
1C042FLYy7rP3MfnkOcnha
(6144, artists    [{'6PAt558ZEZl0DmdXlnjMgD': 'Eric Clapton'}, {...
songid                                618hiI74zBL8UVgAvfmkLj
Name: 6144, dtype: object)
[{'6PAt558ZEZl0DmdXlnjMgD': 'Eric Clapton'}, {'5xLSa7l4IV1gsQfhAMvl0U': 'B.B. King'}]
618hiI74zBL8UVgAvfmkLj
(6145, artists    [{'5xLSa7l4IV1gsQfhAMvl0U': 'B.B. King'}]
songid                        4NQfrmGs9iQXVQI9IpRhjM
Name: 6145, dtype: object)
[{'5xLSa7l4IV1gsQfhAMvl0U': 'B.B. King'}]
4NQfrmGs9iQXVQI9IpRhjM
(6146, artists    [{'4

In [182]:
songartist

id                  songid                artistid
0          0  0VjIjW4GlUZAMYd2vXMi3b  1Xyo4u8uXC1ZmMpatF05PJ
1          1  7qiZfU4dY1lWllzX7mPBI3  6eUKZXaKkcviH0Ku9w2n3V
2          2  7qEHsqek33rTcFNT9PFqLf  4GNC7GD6oZMSxPGyXy4MNB
3          3  2XU0oxnq2qxCpomAAuJY8K  2NjfBq1NflQcKSeiDooVjY
4          4  3KkXRkHbMCARz0aVfEt68P  246dkjvS1zLTtiykXe5h60
...      ...                     ...                     ...
10059  10059  3aeSTu6ejN2BU8YywEcHWO  360IAlyVv4PCEVjgyMZrxK
10060  10060  3KIzaWqMM6wjgVVfcfU5Uj  6Dy7Ex5zlTLgXbsB92rPji
10061  10061  3KIzaWqMM6wjgVVfcfU5Uj  2rRz9oFFpSHCpSTeUzthVI
10062  10062  3KIzaWqMM6wjgVVfcfU5Uj  0ONHkAv9pCAFxb0zJwDNTy
10063  10063  3YR1CSEZrjaCXdvyR1Uj8h  3IaqL9bsZtYJkqNLiovVho

[10064 rows x 3 columns]

In [220]:
artist = pd.DataFrame(columns = ['artistid','artistname'])
artist['temp'] = artists
list(artist['temp'][1].keys())[0]
list(artist['temp'][1].values())[0]
artist['artistid'] = artist.apply(lambda x: list(x['temp'].keys())[0], axis = 1)
artist['artistname'] = artist.apply(lambda x: list(x['temp'].values())[0], axis = 1)
artist = artist.drop_duplicates(['artistid'])
artist = artist.reset_index()
artist.drop('temp', axis = 1, inplace = True)
# topsongs['items'] = topsongs.apply(lambda x: x['info']['tracks']['items'], axis = 1)

In [221]:
artist

index                artistid          artistname
0         0  1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd
1         1  6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran
2         2  4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi
3         3  2NjfBq1NflQcKSeiDooVjY         Tones And I
4         4  246dkjvS1zLTtiykXe5h60         Post Malone
...     ...                     ...                 ...
2301  10053  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti
2302  10055  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell
2303  10060  6Dy7Ex5zlTLgXbsB92rPji                iSHi
2304  10061  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi
2305  10063  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost

[2306 rows x 3 columns]

In [218]:
artist = artist.drop_duplicates(['artistid'])
artist = artist.reset_index()

In [219]:
artist

index                artistid          artistname  \
0         0  1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd   
1         1  6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran   
2         2  4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi   
3         3  2NjfBq1NflQcKSeiDooVjY         Tones And I   
4         4  246dkjvS1zLTtiykXe5h60         Post Malone   
...     ...                     ...                 ...   
2301  10053  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti   
2302  10055  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell   
2303  10060  6Dy7Ex5zlTLgXbsB92rPji                iSHi   
2304  10061  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi   
2305  10063  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost   

                                                  temp  
0             {'1Xyo4u8uXC1ZmMpatF05PJ': 'The Weeknd'}  
1             {'6eUKZXaKkcviH0Ku9w2n3V': 'Ed Sheeran'}  
2          {'4GNC7GD6oZMSxPGyXy4MNB': 'Lewis Capaldi'}  
3            {'2NjfBq1NflQcKSeiDooVjY': 'Tones And I'}  
4            {'246dkjvS1zLTtiykXe5h60': 'Post Malone'}  
...                                                ...  
2301  {'2A4QYjCRttLAzRU4OgchuA': 'Syke Montana Gotti'}  
2302         {'2vGaSKEDFsVPBgcnGxqlBN': 'Alex Newell'}  
2303                {'6Dy7Ex5zlTLgXbsB92rPji': 'iSHi'}  
2304             {'2rRz9oFFpSHCpSTeUzthVI': 'WHOiSHi'}  
2305      {'3IaqL9bsZtYJkqNLiovVho': 'Handsome Ghost'}  

[2306 rows x 4 columns]

Now that I have the song, songartist, and artist tables, I need to get more information for the song and artist tables. For the songs, I want the features, and for the artists, I want the associated genres

In [230]:
results = sp.search(q=f"artist:The Weeknd",type = 'artist', limit = 1)
results#['artist']['items']['genres']

{'artists': {'href': 'https://api.spotify.com/v1/search?query=artist%3AThe+Weeknd&type=artist&offset=0&limit=1',
  'items': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'},
    'followers': {'href': None, 'total': 61407159},
    'genres': ['canadian contemporary r&b', 'canadian pop', 'pop'],
    'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ',
    'id': '1Xyo4u8uXC1ZmMpatF05PJ',
    'images': [{'height': 640,
      'url': 'https://i.scdn.co/image/ab6761610000e5ebb5f9e28219c169fd4b9e8379',
      'width': 640},
     {'height': 320,
      'url': 'https://i.scdn.co/image/ab67616100005174b5f9e28219c169fd4b9e8379',
      'width': 320},
     {'height': 160,
      'url': 'https://i.scdn.co/image/ab6761610000f178b5f9e28219c169fd4b9e8379',
      'width': 160}],
    'name': 'The Weeknd',
    'popularity': 98,
    'type': 'artist',
    'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}],
  'limit': 1,
  'next': 'https://api.spotify.com/v1/s

In [234]:
artist['artistinfo'] = artist.apply(lambda x: sp.search(q=f"artist:{x['artistname']}",type = 'artist', limit = 1), axis = 1)

In [235]:
artist

index                artistid          artistname  \
0         0  1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd   
1         1  6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran   
2         2  4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi   
3         3  2NjfBq1NflQcKSeiDooVjY         Tones And I   
4         4  246dkjvS1zLTtiykXe5h60         Post Malone   
...     ...                     ...                 ...   
2301  10053  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti   
2302  10055  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell   
2303  10060  6Dy7Ex5zlTLgXbsB92rPji                iSHi   
2304  10061  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi   
2305  10063  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost   

                                             aritstinfo  
0     {'artists': {'href': 'https://api.spotify.com/...  
1     {'artists': {'href': 'https://api.spotify.com/...  
2     {'artists': {'href': 'https://api.spotify.com/...  
3     {'artists': {'href': 'https://api.spotify.com/...  
4     {'artists': {'href': 'https://api.spotify.com/...  
...                                                 ...  
2301  {'artists': {'href': 'https://api.spotify.com/...  
2302  {'artists': {'href': 'https://api.spotify.com/...  
2303  {'artists': {'href': 'https://api.spotify.com/...  
2304  {'artists': {'href': 'https://api.spotify.com/...  
2305  {'artists': {'href': 'https://api.spotify.com/...  

[2306 rows x 4 columns]

In [236]:
artist.drop('index', axis = 1, inplace = True)

In [237]:
artist

artistid          artistname  \
0     1Xyo4u8uXC1ZmMpatF05PJ          The Weeknd   
1     6eUKZXaKkcviH0Ku9w2n3V          Ed Sheeran   
2     4GNC7GD6oZMSxPGyXy4MNB       Lewis Capaldi   
3     2NjfBq1NflQcKSeiDooVjY         Tones And I   
4     246dkjvS1zLTtiykXe5h60         Post Malone   
...                      ...                 ...   
2301  2A4QYjCRttLAzRU4OgchuA  Syke Montana Gotti   
2302  2vGaSKEDFsVPBgcnGxqlBN         Alex Newell   
2303  6Dy7Ex5zlTLgXbsB92rPji                iSHi   
2304  2rRz9oFFpSHCpSTeUzthVI             WHOiSHi   
2305  3IaqL9bsZtYJkqNLiovVho      Handsome Ghost   

                                             aritstinfo  
0     {'artists': {'href': 'https://api.spotify.com/...  
1     {'artists': {'href': 'https://api.spotify.com/...  
2     {'artists': {'href': 'https://api.spotify.com/...  
3     {'artists': {'href': 'https://api.spotify.com/...  
4     {'artists': {'href': 'https://api.spotify.com/...  
...                                                 ...  
2301  {'artists': {'href': 'https://api.spotify.com/...  
2302  {'artists': {'href': 'https://api.spotify.com/...  
2303  {'artists': {'href': 'https://api.spotify.com/...  
2304  {'artists': {'href': 'https://api.spotify.com/...  
2305  {'artists': {'href': 'https://api.spotify.com/...  

[2306 rows x 3 columns]

In [244]:
artist['artistinfo'][1]

{'artists': {'href': 'https://api.spotify.com/v1/search?query=artist%3AEd+Sheeran&type=artist&offset=0&limit=1',
  'items': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/6eUKZXaKkcviH0Ku9w2n3V'},
    'followers': {'href': None, 'total': 110663355},
    'genres': ['pop', 'uk pop'],
    'href': 'https://api.spotify.com/v1/artists/6eUKZXaKkcviH0Ku9w2n3V',
    'id': '6eUKZXaKkcviH0Ku9w2n3V',
    'images': [{'height': 640,
      'url': 'https://i.scdn.co/image/ab6761610000e5eb9e690225ad4445530612ccc9',
      'width': 640},
     {'height': 320,
      'url': 'https://i.scdn.co/image/ab676161000051749e690225ad4445530612ccc9',
      'width': 320},
     {'height': 160,
      'url': 'https://i.scdn.co/image/ab6761610000f1789e690225ad4445530612ccc9',
      'width': 160}],
    'name': 'Ed Sheeran',
    'popularity': 92,
    'type': 'artist',
    'uri': 'spotify:artist:6eUKZXaKkcviH0Ku9w2n3V'}],
  'limit': 1,
  'next': 'https://api.spotify.com/v1/search?query=artist%3AEd+Sheeran&ty

In [242]:
artist = artist.rename(columns={'aritstinfo':'artistinfo'})

In [267]:
# artist['followers'] = topsongs.apply(lambda x: x['info']['tracks'], axis = 1)

In [248]:
artist['artistinfo'][1]['artists']['items'][0]

{'external_urls': {'spotify': 'https://open.spotify.com/artist/6eUKZXaKkcviH0Ku9w2n3V'},
 'followers': {'href': None, 'total': 110663355},
 'genres': ['pop', 'uk pop'],
 'href': 'https://api.spotify.com/v1/artists/6eUKZXaKkcviH0Ku9w2n3V',
 'id': '6eUKZXaKkcviH0Ku9w2n3V',
 'images': [{'height': 640,
   'url': 'https://i.scdn.co/image/ab6761610000e5eb9e690225ad4445530612ccc9',
   'width': 640},
  {'height': 320,
   'url': 'https://i.scdn.co/image/ab676161000051749e690225ad4445530612ccc9',
   'width': 320},
  {'height': 160,
   'url': 'https://i.scdn.co/image/ab6761610000f1789e690225ad4445530612ccc9',
   'width': 160}],
 'name': 'Ed Sheeran',
 'popularity': 92,
 'type': 'artist',
 'uri': 'spotify:artist:6eUKZXaKkcviH0Ku9w2n3V'}

In [278]:
artist['followers'] = \
artist.apply(lambda x: x['artistinfo']['artists']['items'][0]['followers']['total'] if len(x['artistinfo']['artists']['items']>0) else np.nan, axis = 1)

TypeError: '>' not supported between instances of 'list' and 'int'

In [264]:
artist['artistinfo'][0]['artists']['items'][0]['followers']['total']

61407159

In [265]:
artist[artist["artistinfo"]=={}]

KeyError: 'aritsts'

In [257]:
artist['artistinfo'].head(2000)

0       {'artists': {'href': 'https://api.spotify.com/...
1       {'artists': {'href': 'https://api.spotify.com/...
2       {'artists': {'href': 'https://api.spotify.com/...
3       {'artists': {'href': 'https://api.spotify.com/...
4       {'artists': {'href': 'https://api.spotify.com/...
                              ...                        
1995    {'artists': {'href': 'https://api.spotify.com/...
1996    {'artists': {'href': 'https://api.spotify.com/...
1997    {'artists': {'href': 'https://api.spotify.com/...
1998    {'artists': {'href': 'https://api.spotify.com/...
1999    {'artists': {'href': 'https://api.spotify.com/...
Name: artistinfo, Length: 2000, dtype: object

In [213]:
artist

NameError: name 'artist' is not defined

In [266]:
for i in artist['artistinfo']:
    print(i)

{'artists': {'href': 'https://api.spotify.com/v1/search?query=artist%3AThe+Weeknd&type=artist&offset=0&limit=1', 'items': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Xyo4u8uXC1ZmMpatF05PJ'}, 'followers': {'href': None, 'total': 61407159}, 'genres': ['canadian contemporary r&b', 'canadian pop', 'pop'], 'href': 'https://api.spotify.com/v1/artists/1Xyo4u8uXC1ZmMpatF05PJ', 'id': '1Xyo4u8uXC1ZmMpatF05PJ', 'images': [{'height': 640, 'url': 'https://i.scdn.co/image/ab6761610000e5ebb5f9e28219c169fd4b9e8379', 'width': 640}, {'height': 320, 'url': 'https://i.scdn.co/image/ab67616100005174b5f9e28219c169fd4b9e8379', 'width': 320}, {'height': 160, 'url': 'https://i.scdn.co/image/ab6761610000f178b5f9e28219c169fd4b9e8379', 'width': 160}], 'name': 'The Weeknd', 'popularity': 98, 'type': 'artist', 'uri': 'spotify:artist:1Xyo4u8uXC1ZmMpatF05PJ'}], 'limit': 1, 'next': 'https://api.spotify.com/v1/search?query=artist%3AThe+Weeknd&type=artist&offset=1&limit=1', 'offset': 0, 'previous': 

In [275]:
artist[artist['artistinfo']=={}]

AttributeError: 'Series' object has no attribute 'artists'

In [2]:
artsit

NameError: name 'artsit' is not defined

In [212]:
artist

NameError: name 'artist' is not defined

In [ ]:
## Short Cut: get artists popularity and rank based on genres

In [216]:
billboard = pd.read_csv("Data/billboard100.csv")

In [217]:
billboard.head()

Unnamed: 0        Date  Rank              Title  \
0           0  1958-08-02     1   Poor Little Fool   
1           1  1958-08-02     2           Patricia   
2           2  1958-08-02     3      Splish Splash   
3           3  1958-08-02     4  Hard Headed Woman   
4           4  1958-08-02     5               When   

                               Artist LastWeek  Peak  WeeksOnChart  
0                        Ricky Nelson        -     1             1  
1       Perez Prado And His Orchestra        -     2             1  
2                         Bobby Darin        -     3             1  
3  Elvis Presley With The Jordanaires        -     4             1  
4                         Kalin Twins        -     5             1

In [220]:
billboard.drop('Unnamed: 0',axis =1, inplace = True)

In [221]:
billboard.head()

Date  Rank              Title                              Artist  \
0  1958-08-02     1   Poor Little Fool                        Ricky Nelson   
1  1958-08-02     2           Patricia       Perez Prado And His Orchestra   
2  1958-08-02     3      Splish Splash                         Bobby Darin   
3  1958-08-02     4  Hard Headed Woman  Elvis Presley With The Jordanaires   
4  1958-08-02     5               When                         Kalin Twins   

  LastWeek  Peak  WeeksOnChart  
0        -     1             1  
1        -     2             1  
2        -     3             1  
3        -     4             1  
4        -     5             1

In [225]:
billboard[['Title','Artist']].value_counts()

Title                 Artist                          
Heat Waves            Glass Animals                       91
Blinding Lights       The Weeknd                          90
Radioactive           Imagine Dragons                     87
Sail                  AWOLNATION                          79
Levitating            Dua Lipa                            77
                                                          ..
Haciendo Que Me Amas  Bad Bunny                            1
Habitual              Justin Bieber                        1
HP                    Maluma                               1
The Float             Hank Ballard And The Midnighters     1
Left Hand Free        alt-J                                1
Length: 30444, dtype: int64